*Setting stuff up*
----------------------------------------

In [1]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_score
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import classification_report, confusion_matrix
import pandas as pd
print(pd.__version__)
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
plt.rcParams['figure.figsize'] = [8,6]
sns.set()
from sklearn.metrics import log_loss
from sklearn.mixture import GaussianMixture
from sklearn.preprocessing import OneHotEncoder
from sklearn.decomposition import PCA

SEED = 1

#import data from csv
#df = pd.read_csv('../data/mp-data1.csv', encoding = "ISO-8859-1")

0.24.2


In [2]:
from sagemaker import get_execution_role

role = get_execution_role()
bucket = 'hockey-project' # Use the name of your s3 bucket here
data_key = 'shots_2007_2018_with_stats.csv'
data_location = 's3://{}/{}'.format(bucket, data_key)

#import data and create X & y sets
df = pd.read_csv(data_location, encoding = "ISO-8859-1")

In [3]:
pd.set_option('display.max_columns', None)
df.head(10)

season  isPlayoffGame  period  goal  xCordAdjusted  yCordAdjusted  \
0    2015              0       3     0             56             20   
1    2015              0       3     0             82             12   
2    2015              0       1     0             63             13   
3    2015              0       1     0             53            -13   
4    2015              0       1     0             42             16   
5    2015              0       2     0             75              0   
6    2015              0       2     0             71             -1   
7    2015              0       2     0             29             -2   
8    2015              1       1     0             51            -13   
9    2015              1       2     0             51            -23   

   shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
0          31.218403              0.000000                          0   
1          59.743563              0.000000                          0   
2          26.565051             26.565051                          0   
3          19.855214              0.000000                          0   
4          18.799885             38.655100                          1   
5           0.000000              0.000000                          0   
6           3.179830              0.000000                          0   
7           1.909152              0.000000                          0   
8          18.886087             18.886087                          0   
9          31.184975              0.000000                          0   

   shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
0     38.587563            0                   0.000000         0   
1     13.892444            0                   0.000000         0   
2     29.068884            0                   8.855017         1   
3     38.275318            0                   0.000000         0   
4     49.648766            0                   3.865510         0   
5     14.000000            0                   0.000000         0   
6     18.027756            0                   0.000000         0   
7     60.033324            0                   0.000000         0   
8     40.162171            0                   2.098454         0   
9     44.418465            0                   0.000000         0   

   speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
0            1.307966            0.000000               0.000000   
1            1.171516            0.000000               0.000000   
2           45.593616            0.000000               0.000000   
3            2.388889            0.000000               0.000000   
4            3.101612          -19.855214              38.275318   
5            1.373249            0.000000               0.000000   
6            3.333333            0.000000               0.000000   
7            0.783746            0.000000               0.000000   
8           12.494443            0.000000               0.000000   
9            1.046267            0.000000               0.000000   

   goalieIdForShot goalieNameForShot  shooterPlayerId        shooterName  \
0          8475299        Joni Ortio          8473548        Phil Kessel   
1          8475299        Joni Ortio          8473548        Phil Kessel   
2          8475660        Cam Talbot          8477591        Josh Jooris   
3          8475299        Joni Ortio          8474034     Patrick Maroon   
4          8475299        Joni Ortio          8471816         Mark Fayne   
5          8475299        Joni Ortio          8474034     Patrick Maroon   
6          8475660        Cam Talbot          8474577       Joe Colborne   
7          8475660        Cam Talbot          8474673          TJ Brodie   
8          8474651     Braden Holtby          8473548        Phil Kessel   
9          8476899       Matt Murray          8473563  Nicklas Backstrom   

   shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  shootingT

In [4]:
df.shape

(1254179, 163)

In [5]:
df['Skater_G_rate'] = df['Skater_G'] / df['Skater_GP']
df['Skater_Ast_rate'] = df['Skater_Ast'] / df['Skater_GP']
df['Skater_Pts_rate'] = df['Skater_Pts'] / df['Skater_GP']
df['Skater_Plus_Minus_rate'] = df['Skater_Plus_Minus'] / df['Skater_GP']
df['Skater_Pen_In_Min_rate'] = df['Skater_Pen_In_Min'] / df['Skater_GP']
df['Skater_PShares_rate'] = df['Skater_PShares'] / df['Skater_GP']
df['Skater_EV_G_rate'] = df['Skater_EV_G'] / df['Skater_GP']
df['Special_Teams_PP_G_rate'] = df['Special_Teams_PP_G'] / df['Skater_GP']
df['Special_Teams_SH_G_rate'] = df['Special_Teams_SH_G'] / df['Skater_GP']
df['Skater_GWinners_rate'] = df['Skater_GWinners'] / df['Skater_GP']
df['Assists_EV_rate'] = df['Assists_EV'] / df['Skater_GP']
df['Assists_PP_rate'] = df['Assists_PP'] / df['Skater_GP']
df['Assists_SH_rate'] = df['Assists_SH'] / df['Skater_GP']
df['Skater_Shots_rate'] = df['Skater_Shots'] / df['Skater_GP']
df['BLK_rate'] = df['BLK'] / df['Skater_GP']
df['HIT_rate'] = df['HIT'] / df['Skater_GP']
df['FOW_rate'] = df['FOW'] / df['Skater_GP']
df['FOL_rate'] = df['FOL'] / df['Skater_GP']
df['Corsi_EV_CF_rate'] = df['Corsi_EV_CF'] / df['Adv_GP']
df['Corsi_EV_CA_rate'] = df['Corsi_EV_CA'] / df['Adv_GP']
df['Fenwick_EV_FF_rate'] = df['Fenwick_EV_FF'] / df['Adv_GP']
df['Fenwick_EV_FA_rate'] = df['Fenwick_EV_FA'] / df['Adv_GP']
df['SAtt_rate'] = df['SAtt'] / df['Adv_GP']


In [7]:
#calculate number of offensive team skaters versus defending team skaters
df['ScoreDiff'] = df['ShootingTeamGoals'] - df['DefendingTeamGoals']

In [8]:
def f(row):
    if row['ScoreDiff'] == 0:
        val = "tied"
    elif row['ScoreDiff'] == 1:
        val = "up1"
    elif row['ScoreDiff'] == 2:
        val = "up2"
    elif row['ScoreDiff'] > 2:
        val = "up3ormore"
    elif row['ScoreDiff'] == -1:
        val = "down1"
    elif row['ScoreDiff'] == -2:
        val = "down2"
    elif row['ScoreDiff'] < -2:
        val = "down3ormore"
    return val

In [9]:
#calculate number of offensive team skaters using the above function
df['ScoreSituation'] = df.apply(f, axis=1)

In [10]:
def rslot(x1,y1,x2,y2,x,y,top,bot):
    slope = (y2-y1)/(x2-x1)
    addedY = slope*(x-x1)
    dividingY = y1 + addedY
    if float(y) >= float(dividingY):
        return(top)
    else:
        return(bot)

def hockeyZones(row):
    x = row['oneSdArenaAdjustedXCord']
    y = row['oneSdArenaAdjustedYCord']
    if x >= 50:
        if y >= 51.5:
            return"R-Point"
        elif y >= 33.5:
            return "C-Point"
        else:
            return "L-Point"
    elif x >= 31:
        if y >= 68.5:
            return "R-1"
        elif y >= 51.5:
            return "R-2"
        elif y >= 33.5:
            return "HighSlot"
        elif y >= 15.5:
            return "L-2"
        else:
            return "L-1"
    elif x >= 11:
        if y >= 68.5:
            return "R-Low"
        elif y >= 51.5:
            return rslot(11,51.5,31,68.5,x,y,"R-Low","R-Slot")
        elif y >= 33.5:
            if x >= 21:
                return "Slot"
            else:
                return "Lowslot"
        elif y >= 15.5:
            return rslot(11,33.5,31,15.5,x,y,"L-Slot","L-Low")
        else:
            return("L-Low")
    else:
        if( y >= 56.8):
            return("R-Back")
        elif y >= 51.5:
            return rslot(0,56.8,11,51.5,x,y,"R-Back","Downlow")
        elif  y >= 33.5:
            return "Downlow"
        elif y >= 28.5:
            return rslot(0,28.5,11,33.5,x,y,"Downlow","L-Back")
        else:
            return "L-Back"

In [11]:
df['Zone'] = df.apply(hockeyZones, axis=1)

In [12]:
#get dummy variables for the categorical ones
df = pd.get_dummies(df, prefix=['ScoreSituation','Zone'], columns=['ScoreSituation','Zone'])

In [13]:
df.head()

season  isPlayoffGame  period  goal  xCordAdjusted  yCordAdjusted  \
0    2015              0       3     0             56             20   
1    2015              0       3     0             82             12   
2    2015              0       1     0             63             13   
3    2015              0       1     0             53            -13   
4    2015              0       1     0             42             16   

   shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
0          31.218403              0.000000                          0   
1          59.743563              0.000000                          0   
2          26.565051             26.565051                          0   
3          19.855214              0.000000                          0   
4          18.799885             38.655100                          1   

   shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
0     38.587563            0                   0.000000         0   
1     13.892444            0                   0.000000         0   
2     29.068884            0                   8.855017         1   
3     38.275318            0                   0.000000         0   
4     49.648766            0                   3.865510         0   

   speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
0            1.307966            0.000000               0.000000   
1            1.171516            0.000000               0.000000   
2           45.593616            0.000000               0.000000   
3            2.388889            0.000000               0.000000   
4            3.101612          -19.855214              38.275318   

   goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
0          8475299        Joni Ortio          8473548     Phil Kessel   
1          8475299        Joni Ortio          8473548     Phil Kessel   
2          8475660        Cam Talbot          8477591     Josh Jooris   
3          8475299        Joni Ortio          8474034  Patrick Maroon   
4          8475299        Joni Ortio          8471816      Mark Fayne   

   shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                53                            53                          5   
1                70                            14                          5   
2                15                            15                          2   
3                20                            20                          3   
4                16                            16                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                            1                          96.0   
1                            1                         113.0   
2                            2                          11.5   
3                            2                          13.2   
4                            2                          23.2   

   shootingTeamAverageTimeOnIceOfForwards  \
0                              104.600000   
1                              121.600000   
2                                8.000000   
3                               15.333333   
4                               25.333333   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                      53.0                       122   
1                                      70.0                       139   
2                                      15.0                        15   
3                                      10.0                        20   
4                                      20.0                        30   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
0                                 122                                    53   
1                                 139                                    70   
2                                  15                  

In [14]:
df = df.fillna(0)

In [15]:
#rearrange data columns to prep for splitting into y and x sets
cols = df.columns.tolist()
cols.insert(0, cols.pop(cols.index('goal')))
cols.insert(1, cols.pop(cols.index('goalieIdForShot')))
cols.insert(2, cols.pop(cols.index('goalieNameForShot')))
cols.insert(3, cols.pop(cols.index('shooterPlayerId')))
cols.insert(4, cols.pop(cols.index('shooterName')))
cols.insert(5, cols.pop(cols.index('uid')))
cols.insert(6, cols.pop(cols.index('xGoal')))
df = df.reindex(columns= cols)
df.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
0     0          8475299        Joni Ortio          8473548     Phil Kessel   
1     0          8475299        Joni Ortio          8473548     Phil Kessel   
2     0          8475660        Cam Talbot          8477591     Josh Jooris   
3     0          8475299        Joni Ortio          8474034  Patrick Maroon   
4     0          8475299        Joni Ortio          8471816      Mark Fayne   

         uid     xGoal  season  isPlayoffGame  period  xCordAdjusted  \
0  201520970  0.048010    2015              0       3             56   
1  201520970  0.084865    2015              0       3             82   
2  201521176  0.124527    2015              0       1             63   
3  201521176  0.025716    2015              0       1             53   
4  201521176  0.013155    2015              0       1             42   

   yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
0             20          31.218403              0.000000   
1             12          59.743563              0.000000   
2             13          26.565051             26.565051   
3            -13          19.855214              0.000000   
4             16          18.799885             38.655100   

   shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
0                          0     38.587563            0   
1                          0     13.892444            0   
2                          0     29.068884            0   
3                          0     38.275318            0   
4                          1     49.648766            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0                   0.000000         0            1.307966   
1                   0.000000         0            1.171516   
2                   8.855017         1           45.593616   
3                   0.000000         0            2.388889   
4                   3.865510         0            3.101612   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0            0.000000               0.000000                53   
1            0.000000               0.000000                70   
2            0.000000               0.000000                15   
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                            53                          5   
1                            14                          5   
2                            15                          2   
3                            20                          3   
4                            16                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                            1                          96.0   
1                            1                         113.0   
2                            2                          11.5   
3                            2                          13.2   
4                            2                          23.2   

   shootingTeamAverageTimeOnIceOfForwards  \
0                              104.600000   
1                              121.600000   
2                                8.000000   
3                               15.333333   
4                               25.333333   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                      53.0                       122   
1                                      70.0                       139   
2                                      15.0                        15   
3                                      10.0                        20   
4                                      20.0                        30   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
0                                 122                   

****Even Strength****
_____________________________________

**Create a Random Sample**

In [16]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
3     0          8475299        Joni Ortio          8474034  Patrick Maroon   
4     0          8475299        Joni Ortio          8471816      Mark Fayne   
5     0          8475299        Joni Ortio          8474034  Patrick Maroon   
6     0          8475660        Cam Talbot          8474577    Joe Colborne   
7     0          8475660        Cam Talbot          8474673       TJ Brodie   

         uid     xGoal  season  isPlayoffGame  period  xCordAdjusted  \
3  201521176  0.025716    2015              0       1             53   
4  201521176  0.013155    2015              0       1             42   
5  201521176  0.133122    2015              0       2             75   
6  201521176  0.101001    2015              0       2             71   
7  201521176  0.020654    2015              0       2             29   

   yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
3            -13          19.855214                0.0000   
4             16          18.799885               38.6551   
5              0           0.000000                0.0000   
6             -1           3.179830                0.0000   
7             -2           1.909152                0.0000   

   shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
3                          0     38.275318            0   
4                          1     49.648766            0   
5                          0     14.000000            0   
6                          0     18.027756            0   
7                          0     60.033324            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
3                    0.00000         0            2.388889   
4                    3.86551         0            3.101612   
5                    0.00000         0            1.373249   
6                    0.00000         0            3.333333   
7                    0.00000         0            0.783746   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   
5            0.000000               0.000000                38   
6            0.000000               0.000000                 6   
7            0.000000               0.000000                42   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
3                            20                          3   
4                            16                          3   
5                            38                          3   
6                             6                          3   
7                            42                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
3                            2                          13.2   
4                            2                          23.2   
5                            2                          26.8   
6                            2                          11.2   
7                            2                          35.4   

   shootingTeamAverageTimeOnIceOfForwards  \
3                               15.333333   
4                               25.333333   
5                               38.000000   
6                                7.666667   
7                               42.000000   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
3                                      10.0                        20   
4                                      20.0                        30   
5                                      10.0                        38   
6                                      16.5                        18   
7                                      25.5                        42   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
3                                  20                   

In [17]:
#randomly sample 10,000 rows
dfs = dftst.sample(15000, random_state=99)

In [18]:
dfs.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
20723       0          8478559  Matthew O'Connor          8471976   
541085      0          8471695       Tuukka Rask          8473426   
326109      0          8468685  Henrik Lundqvist          8470852   
1134676     0          8460806    Dwayne Roloson          8469598   
975670      0          8473404  Niklas Backstrom          8467371   

              shooterName        uid     xGoal  season  isPlayoffGame  period  \
20723    David Desharnais  201520031  0.017234    2015              0       2   
541085         Mike Weber  201020449  0.018076    2010              0       2   
326109       Matt Moulson  201220143  0.082478    2012              0       1   
1134676      Kevin Bieksa  200921038  0.019273    2009              0       1   
975670       Mike Ribeiro  200921220  0.032238    2009              0       3   

         xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
20723               52             35          43.408860   
541085              32            -27          25.346176   
326109              75              4          15.945396   
1134676             33              9           9.130176   
975670              51             20          27.758541   

         shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
20723                     0.0                          0     50.931326   
541085                    0.0                          0     63.071388   
326109                    0.0                          0     14.560220   
1134676                   0.0                          0     56.718604   
975670                    0.0                          0     42.941821   

         shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
20723              0                        0.0         0           11.704700   
541085             0                        0.0         0            9.334077   
326109             0                        0.0         0            3.721042   
1134676            0                        0.0         0            3.547240   
975670             0                        0.0         0            6.624474   

         lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
20723                   0.0                    0.0                45   
541085                  0.0                    0.0                 4   
326109                  0.0                    0.0                 9   
1134676                 0.0                    0.0                23   
975670                  0.0                    0.0                57   

         shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
20723                              45                          3   
541085                              4                          3   
326109                              9                          3   
1134676                            23                          3   
975670                             19                          4   

         shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
20723                              2                          45.0   
541085                             2                           4.0   
326109                             2                          16.2   
1134676                            2                          22.6   
975670                             1                          63.2   

         shootingTeamAverageTimeOnIceOfForwards  \
20723                                 45.000000   
541085                                 4.000000   
326109                                 9.000000   
1134676                               28.666667   
975670                                77.500000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
20723                                        45.0                        45   
541085                                        4.0                         4   
326109 

In [19]:
#create x & y sets on the 10,000 samples
y_train = dfs.iloc[:,0]
X_train = dfs.iloc[:,8:]
X_train.shape

(15000, 197)

In [20]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  \
20723                0       2             52             35   
541085               0       2             32            -27   
326109               0       1             75              4   
1134676              0       1             33              9   
975670               0       3             51             20   

         shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
20723            43.408860                   0.0                          0   
541085           25.346176                   0.0                          0   
326109           15.945396                   0.0                          0   
1134676           9.130176                   0.0                          0   
975670           27.758541                   0.0                          0   

         shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
20723       50.931326            0                        0.0         0   
541085      63.071388            0                        0.0         0   
326109      14.560220            0                        0.0         0   
1134676     56.718604            0                        0.0         0   
975670      42.941821            0                        0.0         0   

         speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
20723             11.704700                 0.0                    0.0   
541085             9.334077                 0.0                    0.0   
326109             3.721042                 0.0                    0.0   
1134676            3.547240                 0.0                    0.0   
975670             6.624474                 0.0                    0.0   

         shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  \
20723                  45                            45   
541085                  4                             4   
326109                  9                             9   
1134676                23                            23   
975670                 57                            19   

         shootingTeamForwardsOnIce  shootingTeamDefencemenOnIce  \
20723                            3                            2   
541085                           3                            2   
326109                           3                            2   
1134676                          3                            2   
975670                           4                            1   

         shootingTeamAverageTimeOnIce  shootingTeamAverageTimeOnIceOfForwards  \
20723                            45.0                               45.000000   
541085                            4.0                                4.000000   
326109                           16.2                                9.000000   
1134676                          22.6                               28.666667   
975670                           63.2                               77.500000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
20723                                        45.0                        45   
541085                                        4.0                         4   
326109                                       27.0                        27   
1134676                                      13.5                        40   
975670                                        6.0                       121   

         shootingTeamMaxTimeOnIceOfForwards  \
20723                                    45   
541085                                    4   
326109                                   15   
1134676                                  40   
975670                                  121   

         shootingTeamMaxTimeOnIceOfDefencemen  shootingTeamMinTimeOnIce  \
20723                                      45                        45   
541085                                      4                         4   
326109                   

In [21]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dfnew.shape

(93051, 205)

In [22]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(93051, 197)

**XGBoost for feature selection**

In [23]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16,
                    min_child_weight= 50,
                    n_estimators= 7500,
                    learning_rate = 0.001,
                    subsample= 0.8,
                    max_depth= 7
                   )

best = xgb.fit(X_train, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
both = zip(list(best.feature_importances_),X_train.columns)
ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
ndf.sort_values('Importance',ascending=False,inplace=True)
print(ndf)

     Importance                                            Feature
77     0.044505                                        Square_dist
57     0.024675                          arenaAdjustedShotDistance
76     0.021292                                       Rebound_dist
8      0.019768                                        shotRebound
79     0.016725                                         Square_all
75     0.016725                                         Dist_angle
60     0.015533                              arenaAdjustedYCordAbs
7      0.009891                                       shotDistance
78     0.008567                                       Square_angle
70     0.008208                                          Back_dist
6      0.008066                          shotAngleReboundRoyalRoad
88     0.008053                                      shotsWithin60
92     0.007913                                      shotType_SNAP
71     0.007586                                         Quick_

In [28]:
ndnew = ndf['Feature'][ndf['Importance'] > 0.006].tolist()
ndnew

['Square_dist',
 'arenaAdjustedShotDistance',
 'Rebound_dist',
 'shotRebound',
 'Square_all',
 'Dist_angle',
 'arenaAdjustedYCordAbs',
 'shotDistance',
 'Square_angle',
 'Back_dist',
 'shotAngleReboundRoyalRoad',
 'shotsWithin60',
 'shotType_SNAP',
 'Quick_dist',
 'shotAngleAdjusted',
 'shotAnglePlusReboundSpeed',
 'speedFromLastEvent',
 'shootingTeamMaxTimeOnIceOfDefencemen',
 'oneSdArenaAdjustedYCord',
 'shotType_BACK',
 'oiSH_PCT',
 'PDO',
 'yCordAdjusted',
 'shootingTeamAverageTimeOnIceOfDefencemen',
 'defendingTeamMaxTimeOnIceOfForwardsSinceFaceoff',
 'BLK',
 'shootingTeamAverageTimeOnIceOfDefencemenSinceFaceoff',
 'Zone_L-Back',
 'shootingTeamMinTimeOnIceOfDefencemen',
 'Special_Teams_SH_G_rate',
 'defendingTeamAverageTimeOnIceOfDefencemen',
 'shootingTeamMinTimeOnIceOfDefencemenSinceFaceoff',
 'defendingTeamAverageTimeOnIceSinceFaceoff',
 'period',
 'oneSdArenaAdjustedXCord',
 'Assists_SH',
 'defendingTeamAverageTimeOnIceOfDefencemenSinceFaceoff',
 'Fenwick_EV_FA',
 'shotAnglePl

In [29]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
3     0          8475299        Joni Ortio          8474034  Patrick Maroon   
4     0          8475299        Joni Ortio          8471816      Mark Fayne   
5     0          8475299        Joni Ortio          8474034  Patrick Maroon   
6     0          8475660        Cam Talbot          8474577    Joe Colborne   
7     0          8475660        Cam Talbot          8474673       TJ Brodie   

         uid     xGoal  season  isPlayoffGame  period  xCordAdjusted  \
3  201521176  0.025716    2015              0       1             53   
4  201521176  0.013155    2015              0       1             42   
5  201521176  0.133122    2015              0       2             75   
6  201521176  0.101001    2015              0       2             71   
7  201521176  0.020654    2015              0       2             29   

   yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
3            -13          19.855214                0.0000   
4             16          18.799885               38.6551   
5              0           0.000000                0.0000   
6             -1           3.179830                0.0000   
7             -2           1.909152                0.0000   

   shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
3                          0     38.275318            0   
4                          1     49.648766            0   
5                          0     14.000000            0   
6                          0     18.027756            0   
7                          0     60.033324            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
3                    0.00000         0            2.388889   
4                    3.86551         0            3.101612   
5                    0.00000         0            1.373249   
6                    0.00000         0            3.333333   
7                    0.00000         0            0.783746   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   
5            0.000000               0.000000                38   
6            0.000000               0.000000                 6   
7            0.000000               0.000000                42   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
3                            20                          3   
4                            16                          3   
5                            38                          3   
6                             6                          3   
7                            42                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
3                            2                          13.2   
4                            2                          23.2   
5                            2                          26.8   
6                            2                          11.2   
7                            2                          35.4   

   shootingTeamAverageTimeOnIceOfForwards  \
3                               15.333333   
4                               25.333333   
5                               38.000000   
6                                7.666667   
7                               42.000000   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
3                                      10.0                        20   
4                                      20.0                        30   
5                                      10.0                        38   
6                                      16.5                        18   
7                                      25.5                        42   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
3                                  20                   

In [30]:
#randomly sample 10,000 rows
dfs = dftst.sample(100000, random_state=99)

In [31]:
dfs.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
20723       0          8478559  Matthew O'Connor          8471976   
541085      0          8471695       Tuukka Rask          8473426   
326109      0          8468685  Henrik Lundqvist          8470852   
1134676     0          8460806    Dwayne Roloson          8469598   
975670      0          8473404  Niklas Backstrom          8467371   

              shooterName        uid     xGoal  season  isPlayoffGame  period  \
20723    David Desharnais  201520031  0.017234    2015              0       2   
541085         Mike Weber  201020449  0.018076    2010              0       2   
326109       Matt Moulson  201220143  0.082478    2012              0       1   
1134676      Kevin Bieksa  200921038  0.019273    2009              0       1   
975670       Mike Ribeiro  200921220  0.032238    2009              0       3   

         xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
20723               52             35          43.408860   
541085              32            -27          25.346176   
326109              75              4          15.945396   
1134676             33              9           9.130176   
975670              51             20          27.758541   

         shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
20723                     0.0                          0     50.931326   
541085                    0.0                          0     63.071388   
326109                    0.0                          0     14.560220   
1134676                   0.0                          0     56.718604   
975670                    0.0                          0     42.941821   

         shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
20723              0                        0.0         0           11.704700   
541085             0                        0.0         0            9.334077   
326109             0                        0.0         0            3.721042   
1134676            0                        0.0         0            3.547240   
975670             0                        0.0         0            6.624474   

         lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
20723                   0.0                    0.0                45   
541085                  0.0                    0.0                 4   
326109                  0.0                    0.0                 9   
1134676                 0.0                    0.0                23   
975670                  0.0                    0.0                57   

         shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
20723                              45                          3   
541085                              4                          3   
326109                              9                          3   
1134676                            23                          3   
975670                             19                          4   

         shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
20723                              2                          45.0   
541085                             2                           4.0   
326109                             2                          16.2   
1134676                            2                          22.6   
975670                             1                          63.2   

         shootingTeamAverageTimeOnIceOfForwards  \
20723                                 45.000000   
541085                                 4.000000   
326109                                 9.000000   
1134676                               28.666667   
975670                                77.500000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
20723                                        45.0                        45   
541085                                        4.0                         4   
326109 

In [32]:
#create x & y sets on the 10,000 samples
y_train = dfs.iloc[:,0]
X_train = dfs.iloc[:,8:]
X_train.shape

(100000, 197)

In [33]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  \
20723                0       2             52             35   
541085               0       2             32            -27   
326109               0       1             75              4   
1134676              0       1             33              9   
975670               0       3             51             20   

         shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
20723            43.408860                   0.0                          0   
541085           25.346176                   0.0                          0   
326109           15.945396                   0.0                          0   
1134676           9.130176                   0.0                          0   
975670           27.758541                   0.0                          0   

         shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
20723       50.931326            0                        0.0         0   
541085      63.071388            0                        0.0         0   
326109      14.560220            0                        0.0         0   
1134676     56.718604            0                        0.0         0   
975670      42.941821            0                        0.0         0   

         speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
20723             11.704700                 0.0                    0.0   
541085             9.334077                 0.0                    0.0   
326109             3.721042                 0.0                    0.0   
1134676            3.547240                 0.0                    0.0   
975670             6.624474                 0.0                    0.0   

         shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  \
20723                  45                            45   
541085                  4                             4   
326109                  9                             9   
1134676                23                            23   
975670                 57                            19   

         shootingTeamForwardsOnIce  shootingTeamDefencemenOnIce  \
20723                            3                            2   
541085                           3                            2   
326109                           3                            2   
1134676                          3                            2   
975670                           4                            1   

         shootingTeamAverageTimeOnIce  shootingTeamAverageTimeOnIceOfForwards  \
20723                            45.0                               45.000000   
541085                            4.0                                4.000000   
326109                           16.2                                9.000000   
1134676                          22.6                               28.666667   
975670                           63.2                               77.500000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
20723                                        45.0                        45   
541085                                        4.0                         4   
326109                                       27.0                        27   
1134676                                      13.5                        40   
975670                                        6.0                       121   

         shootingTeamMaxTimeOnIceOfForwards  \
20723                                    45   
541085                                    4   
326109                                   15   
1134676                                  40   
975670                                  121   

         shootingTeamMaxTimeOnIceOfDefencemen  shootingTeamMinTimeOnIce  \
20723                                      45                        45   
541085                                      4                         4   
326109                   

In [34]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dfnew.shape

(93051, 205)

In [35]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(93051, 197)

In [36]:
X1 = X_train[ndnew]
X1.shape

(100000, 51)

In [37]:
X1_test = X_test[ndnew]
X1_test.shape

(93051, 51)

**Create clusters and add to the dataset**

In [38]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)
#gaus = GaussianMixture(n_components=2, random_state=0).fit_predict(pca_rf)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


In [39]:
selector.shape

(100000, 56)

**XGBoost for hyperparameter tuning**

In [ ]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16)

#set parmeter grid
params = {
        'min_child_weight': [10,50,100],
        'n_estimators': [3500,5000,7500],
        'learning_rate' : [0.001],
        'subsample': [0.5],
        'max_depth': [4,5,6,7,8]
        }

#create GridSearchCV object and fit it versus training data
grid = GridSearchCV(estimator=xgb, param_grid=params, scoring='neg_log_loss', n_jobs=-1, cv=5, verbose=10 )
grid.fit(selector, y_train)

#extract the best params from 'grid'
best_hyperparams = grid.best_params_
print(best_hyperparams)

#extract best CV score 
best_CV_score = grid.best_score_
print(best_CV_score)

#extract best model from grid
best_xg = grid.best_estimator_

#Fit the model to the data
best = best_xg.fit(selector,y_train)

#make predictions on test data
y_pred = best.predict(selector_test)
predictions = [round(value) for value in y_pred]

#create confusion & classification matrix
from sklearn.metrics import classification_report,confusion_matrix
print(confusion_matrix(y_test,predictions))
print(classification_report(y_test,predictions,digits=3))

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

Fitting 5 folds for each of 45 candidates, totalling 225 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 36 concurrent workers.
[Parallel(n_jobs=-1)]: Done  13 tasks      | elapsed:  4.7min
[Parallel(n_jobs=-1)]: Done  41 tasks      | elapsed: 10.7min
[Parallel(n_jobs=-1)]: Done  56 tasks      | elapsed: 15.3min
[Parallel(n_jobs=-1)]: Done  73 tasks      | elapsed: 19.3min
[Parallel(n_jobs=-1)]: Done  90 tasks      | elapsed: 22.9min
[Parallel(n_jobs=-1)]: Done 109 tasks      | elapsed: 27.7min
[Parallel(n_jobs=-1)]: Done 128 tasks      | elapsed: 33.7min
[Parallel(n_jobs=-1)]: Done 149 tasks      | elapsed: 38.7min
[Parallel(n_jobs=-1)]: Done 177 out of 225 | elapsed: 47.7min remaining: 12.9min
[Parallel(n_jobs=-1)]: Done 223 out of 225 | elapsed: 58.5min remaining:   31.5s
[Parallel(n_jobs=-1)]: Done 225 out of 225 | elapsed: 59.3min finished


{'learning_rate': 0.001, 'max_depth': 6, 'min_child_weight': 10, 'n_estimators': 7500, 'subsample': 0.5}
-0.19238266506509158
[[87571    12]
 [ 5464     4]]
              precision    recall  f1-score   support

           0      0.941     1.000     0.970     87583
           1      0.250     0.001     0.001      5468

   micro avg      0.941     0.941     0.941     93051
   macro avg      0.596     0.500     0.486     93051
weighted avg      0.901     0.941     0.913     93051



array([0.0100546 , 0.00994855, 0.01226097, 0.00823341, 0.00995508,
       0.06855017, 0.10958246, 0.01314082, 0.1127094 , 0.01952191,
       0.03046944, 0.02582816, 0.05705298, 0.01461855, 0.01682899,
       0.02375586, 0.01118408, 0.01228763, 0.02010033, 0.01325096,
       0.01420641, 0.01238395, 0.01041069, 0.01106201, 0.01325403,
       0.01035299, 0.01059288, 0.01065513, 0.01086043, 0.01057572,
       0.01030866, 0.01224616, 0.00976191, 0.01190911, 0.01040571,
       0.01051217, 0.01149783, 0.01025675, 0.0114069 , 0.01037563,
       0.01051977, 0.01051146, 0.01065437, 0.01255746, 0.01100722,
       0.01094113, 0.01085768, 0.01082494, 0.01136112, 0.01051294,
       0.01185666, 0.01040155, 0.0102014 , 0.01289866, 0.01320173,
       0.00932247], dtype=float32)

In [42]:
predictions_prob = best.predict_proba(selector_test)

In [43]:
print(predictions_prob)

[[0.9800722  0.01992782]
 [0.9520882  0.0479118 ]
 [0.9916406  0.00835937]
 ...
 [0.9754676  0.02453236]
 [0.98261744 0.01738258]
 [0.93570745 0.06429254]]


In [44]:
print(log_loss(y_test,predictions_prob[:,1]))

0.1981026897439916


**XGBoost trained against all observations pre-2017**

In [29]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
3     0          8475299        Joni Ortio          8474034  Patrick Maroon   
4     0          8475299        Joni Ortio          8471816      Mark Fayne   
5     0          8475299        Joni Ortio          8474034  Patrick Maroon   
6     0          8475660        Cam Talbot          8474577    Joe Colborne   
7     0          8475660        Cam Talbot          8474673       TJ Brodie   

         uid     xGoal  season  isPlayoffGame  period  xCordAdjusted  \
3  201521176  0.025716    2015              0       1             53   
4  201521176  0.013155    2015              0       1             42   
5  201521176  0.133122    2015              0       2             75   
6  201521176  0.101001    2015              0       2             71   
7  201521176  0.020654    2015              0       2             29   

   yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
3            -13          19.855214                0.0000   
4             16          18.799885               38.6551   
5              0           0.000000                0.0000   
6             -1           3.179830                0.0000   
7             -2           1.909152                0.0000   

   shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
3                          0     38.275318            0   
4                          1     49.648766            0   
5                          0     14.000000            0   
6                          0     18.027756            0   
7                          0     60.033324            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
3                    0.00000         0            2.388889   
4                    3.86551         0            3.101612   
5                    0.00000         0            1.373249   
6                    0.00000         0            3.333333   
7                    0.00000         0            0.783746   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   
5            0.000000               0.000000                38   
6            0.000000               0.000000                 6   
7            0.000000               0.000000                42   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
3                            20                          3   
4                            16                          3   
5                            38                          3   
6                             6                          3   
7                            42                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
3                            2                          13.2   
4                            2                          23.2   
5                            2                          26.8   
6                            2                          11.2   
7                            2                          35.4   

   shootingTeamAverageTimeOnIceOfForwards  \
3                               15.333333   
4                               25.333333   
5                               38.000000   
6                                7.666667   
7                               42.000000   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
3                                      10.0                        20   
4                                      20.0                        30   
5                                      10.0                        38   
6                                      16.5                        18   
7                                      25.5                        42   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
3                                  20                   

In [45]:
#create x & y sets on the 10,000 samples
y_train = dftst.iloc[:,0]
X_train = dftst.iloc[:,8:]
X_train.shape

(654288, 197)

In [46]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
3              0       1             53            -13          19.855214   
4              0       1             42             16          18.799885   
5              0       2             75              0           0.000000   
6              0       2             71             -1           3.179830   
7              0       2             29             -2           1.909152   

   shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
3                0.0000                          0     38.275318            0   
4               38.6551                          1     49.648766            0   
5                0.0000                          0     14.000000            0   
6                0.0000                          0     18.027756            0   
7                0.0000                          0     60.033324            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
3                    0.00000         0            2.388889   
4                    3.86551         0            3.101612   
5                    0.00000         0            1.373249   
6                    0.00000         0            3.333333   
7                    0.00000         0            0.783746   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   
5            0.000000               0.000000                38   
6            0.000000               0.000000                 6   
7            0.000000               0.000000                42   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
3                            20                          3   
4                            16                          3   
5                            38                          3   
6                             6                          3   
7                            42                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
3                            2                          13.2   
4                            2                          23.2   
5                            2                          26.8   
6                            2                          11.2   
7                            2                          35.4   

   shootingTeamAverageTimeOnIceOfForwards  \
3                               15.333333   
4                               25.333333   
5                               38.000000   
6                                7.666667   
7                               42.000000   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
3                                      10.0                        20   
4                                      20.0                        30   
5                                      10.0                        38   
6                                      16.5                        18   
7                                      25.5                        42   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
3                                  20                                    14   
4                                  30                                    24   
5                                  38                                    10   
6                                  11                                    18   
7                                  42                                    42   

   shootingTeamMinTimeOnIce  shootingTeamMinTimeOnIceOfForwards  \
3                         6                                   6   
4                        16                                  16   
5                        10                                  38   
6                         6                                   6   
7    

In [47]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dfnew.shape

(93051, 205)

In [48]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(93051, 197)

In [49]:
X1 = X_train[ndnew]
X1.shape

(654288, 51)

In [50]:
X1_test = X_test[ndnew]
X1_test.shape

(93051, 51)

In [51]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)
selector.ndim


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


AttributeError: 'numpy.ndarray' object has no attribute 'dim'

In [ ]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=32,
                    min_child_weight= 25,
                    n_estimators= 7500,
                    learning_rate = 0.001,
                    subsample= 0.6,
                    max_depth= 6
                   )

best = xgb.fit(selector, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

array([0.00798705, 0.00395031, 0.00704523, 0.01370817, 0.00718697,
       0.07895263, 0.18258578, 0.01341587, 0.23248978, 0.03409639,
       0.        , 0.04639744, 0.        , 0.01208755, 0.01496646,
       0.05184018, 0.00544533, 0.01396801, 0.02351683, 0.        ,
       0.01149704, 0.01368384, 0.00685451, 0.00524128, 0.01061981,
       0.00562107, 0.00522145, 0.00634008, 0.00596501, 0.00588634,
       0.00575364, 0.00745944, 0.00578989, 0.00631186, 0.00604955,
       0.0051996 , 0.00793388, 0.00593616, 0.00761948, 0.00595722,
       0.00555506, 0.00547257, 0.00522471, 0.0068207 , 0.0050967 ,
       0.00516281, 0.00502197, 0.00500958, 0.00738512, 0.01017448,
       0.0116521 , 0.00514757, 0.00473961, 0.01108392, 0.00892697,
       0.00694503], dtype=float32)

In [54]:
predictions_prob = best.predict_proba(selector_test)
print(log_loss(y_test,predictions_prob[:,1]))

0.19700520427432036


***Now Estimate All Even Strength Shots Using the Final Model***

In [55]:
#create test set based on shots before 2017-18
dffinal = df[((df['situation_5on5'] == 1) | (df['situation_4on4'] == 1) | (df['situation_3on3'] == 1))]
dffinal.shape

(998130, 205)

In [56]:
#create x & y sets on the 10,000 samples
y_test = dffinal.iloc[:,0]
X_test = dffinal.iloc[:,8:]
X_test.shape

(998130, 197)

In [57]:
X1 = X_test[ndnew]
X1.shape

(998130, 51)

In [58]:
pca_r = pca_rf.transform(X1)
gaus_pc = gaus_pcarfe.predict(pca_r)
C = gaus_pc.reshape(-1, 1)
B = A.transform(C)
selector_final = np.concatenate((B, X1), axis=1)
selector_final.ndim

2

In [59]:
predictions_prob = best.predict_proba(selector_final)
print(log_loss(y_test,predictions_prob[:,1]))

0.1912002890243084


In [61]:
dffinal['xGoal_GT'] = predictions_prob[:,1]
dffinal.head()

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


goal  goalieIdForShot goalieNameForShot  shooterPlayerId     shooterName  \
3     0          8475299        Joni Ortio          8474034  Patrick Maroon   
4     0          8475299        Joni Ortio          8471816      Mark Fayne   
5     0          8475299        Joni Ortio          8474034  Patrick Maroon   
6     0          8475660        Cam Talbot          8474577    Joe Colborne   
7     0          8475660        Cam Talbot          8474673       TJ Brodie   

         uid     xGoal  season  isPlayoffGame  period  xCordAdjusted  \
3  201521176  0.025716    2015              0       1             53   
4  201521176  0.013155    2015              0       1             42   
5  201521176  0.133122    2015              0       2             75   
6  201521176  0.101001    2015              0       2             71   
7  201521176  0.020654    2015              0       2             29   

   yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
3            -13          19.855214                0.0000   
4             16          18.799885               38.6551   
5              0           0.000000                0.0000   
6             -1           3.179830                0.0000   
7             -2           1.909152                0.0000   

   shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
3                          0     38.275318            0   
4                          1     49.648766            0   
5                          0     14.000000            0   
6                          0     18.027756            0   
7                          0     60.033324            0   

   shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
3                    0.00000         0            2.388889   
4                    3.86551         0            3.101612   
5                    0.00000         0            1.373249   
6                    0.00000         0            3.333333   
7                    0.00000         0            0.783746   

   lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
3            0.000000               0.000000                20   
4          -19.855214              38.275318                16   
5            0.000000               0.000000                38   
6            0.000000               0.000000                 6   
7            0.000000               0.000000                42   

   shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
3                            20                          3   
4                            16                          3   
5                            38                          3   
6                             6                          3   
7                            42                          3   

   shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
3                            2                          13.2   
4                            2                          23.2   
5                            2                          26.8   
6                            2                          11.2   
7                            2                          35.4   

   shootingTeamAverageTimeOnIceOfForwards  \
3                               15.333333   
4                               25.333333   
5                               38.000000   
6                                7.666667   
7                               42.000000   

   shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
3                                      10.0                        20   
4                                      20.0                        30   
5                                      10.0                        38   
6                                      16.5                        18   
7                                      25.5                        42   

   shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
3                                  20                   

****Power Play****
_____________________________________

**Create a Random Sample**

In [62]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
0      0          8475299        Joni Ortio          8473548   
1      0          8475299        Joni Ortio          8473548   
9      0          8476899       Matt Murray          8473563   
12     0          8476899       Matt Murray          8473563   
13     0          8475660        Cam Talbot          8478562   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
0         Phil Kessel  201520970  0.048010    2015              0       3   
1         Phil Kessel  201520970  0.084865    2015              0       3   
9   Nicklas Backstrom  201530225  0.040731    2015              1       2   
12  Nicklas Backstrom  201530225  0.086180    2015              1       2   
13     Jakub Nakladal  201521176  0.004383    2015              0       2   

    xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
0              56             20          31.218403                   0.0   
1              82             12          59.743563                   0.0   
9              51            -23          31.184975                   0.0   
12             61            -11          21.447736                   0.0   
13             34            -19          19.057705                   0.0   

    shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
0                           0     38.587563            0   
1                           0     13.892444            0   
9                           0     44.418465            0   
12                          0     30.083218            0   
13                          0     58.189346            0   

    shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0                         0.0         0            1.307966   
1                         0.0         0            1.171516   
9                         0.0         0            1.046267   
12                        0.0         0            2.600000   
13                        0.0         0            0.950323   

    lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0                  0.0                    0.0                53   
1                  0.0                    0.0                70   
9                  0.0                    0.0                47   
12                 0.0                    0.0                10   
13                 0.0                    0.0                17   

    shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                             53                          5   
1                             14                          5   
9                             47                          4   
12                            10                          4   
13                            17                          3   

    shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                             1                          96.0   
1                             1                         113.0   
9                             1                          47.0   
12                            1                          18.0   
13                            2                          27.0   

    shootingTeamAverageTimeOnIceOfForwards  \
0                               104.600000   
1                               121.600000   
9                                47.000000   
12                               12.000000   
13                               25.333333   

    shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                       53.0                       122   
1                                       70.0                       139   
9                                       47.0                        47   
12                                      42.0                        42   
13                                      29.5                        42   

    shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTim

In [63]:
#randomly sample 10,000 rows
dfs = dftst.sample(15000, random_state=99)

In [64]:
dfs.head()

goal  goalieIdForShot  goalieNameForShot  shooterPlayerId  \
896280      0          8473503       James Reimer          8474161   
858216      0          8469514        Peter Budaj          8470642   
800773      0          8474651      Braden Holtby          8470616   
1004464     0          8470594  Marc-Andre Fleury          8470309   
460311      0          8470860     Jaroslav Halak          8475169   

           shooterName        uid     xGoal  season  isPlayoffGame  period  \
896280   Jakub Voracek  201620385  0.058278    2016              0       2   
858216      Shea Weber  201620377  0.005247    2016              0       4   
800773     Ryan Kesler  201621014  0.307963    2016              0       3   
1004464   Ryan Whitney  200920202  0.032204    2009              0       2   
460311    Evander Kane  201020149  0.555098    2010              0       3   

         xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
896280              64            -25          45.000000   
858216              43             16          19.179008   
800773              81              2          14.036243   
1004464             45             -6           7.765166   
460311              78            -16          55.491477   

         shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
896280                    0.0                          0     35.355339   
858216                    0.0                          0     48.703183   
800773                    0.0                          0      8.246211   
1004464                   0.0                          0     44.407207   
460311                    0.0                          0     19.416488   

         shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
896280             0                        0.0         0            3.938767   
858216             0                        0.0         0            1.905952   
800773             0                        0.0         0            3.605551   
1004464            0                        0.0         0            1.143959   
460311             0                        0.0         0            0.600925   

         lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
896280                  0.0                    0.0                12   
858216                  0.0                    0.0                59   
800773                  0.0                    0.0                27   
1004464                 0.0                    0.0                91   
460311                  0.0                    0.0                18   

         shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
896280                             12                          4   
858216                             14                          3   
800773                             27                          4   
1004464                            68                          3   
460311                             18                          4   

         shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
896280                             1                         12.00   
858216                             1                         27.75   
800773                             1                         59.80   
1004464                            2                         80.20   
460311                             1                         68.80   

         shootingTeamAverageTimeOnIceOfForwards  \
896280                                12.000000   
858216                                17.333333   
800773                                68.000000   
1004464                               55.666667   
460311                                27.750000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
896280                                       12.0                        12   
858216                                       59.0                        59   
800773             

In [65]:
#create x & y sets on the 10,000 samples
y_train = dfs.iloc[:,0]
X_train = dfs.iloc[:,8:]
X_train.shape

(15000, 197)

In [66]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  \
896280               0       2             64            -25   
858216               0       4             43             16   
800773               0       3             81              2   
1004464              0       2             45             -6   
460311               0       3             78            -16   

         shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
896280           45.000000                   0.0                          0   
858216           19.179008                   0.0                          0   
800773           14.036243                   0.0                          0   
1004464           7.765166                   0.0                          0   
460311           55.491477                   0.0                          0   

         shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
896280      35.355339            0                        0.0         0   
858216      48.703183            0                        0.0         0   
800773       8.246211            0                        0.0         0   
1004464     44.407207            0                        0.0         0   
460311      19.416488            0                        0.0         0   

         speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
896280             3.938767                 0.0                    0.0   
858216             1.905952                 0.0                    0.0   
800773             3.605551                 0.0                    0.0   
1004464            1.143959                 0.0                    0.0   
460311             0.600925                 0.0                    0.0   

         shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  \
896280                 12                            12   
858216                 59                            14   
800773                 27                            27   
1004464                91                            68   
460311                 18                            18   

         shootingTeamForwardsOnIce  shootingTeamDefencemenOnIce  \
896280                           4                            1   
858216                           3                            1   
800773                           4                            1   
1004464                          3                            2   
460311                           4                            1   

         shootingTeamAverageTimeOnIce  shootingTeamAverageTimeOnIceOfForwards  \
896280                          12.00                               12.000000   
858216                          27.75                               17.333333   
800773                          59.80                               68.000000   
1004464                         80.20                               55.666667   
460311                          68.80                               27.750000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
896280                                       12.0                        12   
858216                                       59.0                        59   
800773                                       27.0                       106   
1004464                                     117.0                       143   
460311                                      233.0                       233   

         shootingTeamMaxTimeOnIceOfForwards  \
896280                                   12   
858216                                   24   
800773                                  106   
1004464                                  76   
460311                                   57   

         shootingTeamMaxTimeOnIceOfDefencemen  shootingTeamMinTimeOnIce  \
896280                                     12                        12   
858216                                     59                        14   
800773                   

In [67]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dfnew.shape

(19694, 205)

In [68]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(19694, 197)

**XGBoost for feature selection**

In [69]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16,
                    min_child_weight= 25,
                    n_estimators= 7500,
                    learning_rate = 0.001,
                    subsample= 0.8,
                    max_depth= 7
                   )

best = xgb.fit(X_train, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
both = zip(list(best.feature_importances_),X_train.columns)
ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
ndf.sort_values('Importance',ascending=False,inplace=True)
print(ndf)

     Importance                                            Feature
57     0.028452                          arenaAdjustedShotDistance
77     0.024534                                        Square_dist
8      0.020811                                        shotRebound
7      0.011773                                       shotDistance
9      0.010153                          shotAnglePlusReboundSpeed
6      0.008217                          shotAngleReboundRoyalRoad
68     0.007671                               DefendingTeamSkaters
92     0.007427                                      shotType_SNAP
76     0.007425                                       Rebound_dist
71     0.007245                                         Quick_dist
70     0.007219                                          Back_dist
5      0.006914                               shotAnglePlusRebound
69     0.006884                                         SkaterDiff
89     0.006721                                      shotType_

In [76]:
ndnew = ndf['Feature'][ndf['Importance'] > 0.0056].tolist()
ndnew

['arenaAdjustedShotDistance',
 'Square_dist',
 'shotRebound',
 'shotDistance',
 'shotAnglePlusReboundSpeed',
 'shotAngleReboundRoyalRoad',
 'DefendingTeamSkaters',
 'shotType_SNAP',
 'Rebound_dist',
 'Quick_dist',
 'Back_dist',
 'shotAnglePlusRebound',
 'SkaterDiff',
 'shotType_BACK',
 'ScoreSituation_up2',
 'Dist_angle',
 'Special_Teams_SH_G',
 'shotType_WRIST',
 'defendingTeamMaxTimeOnIceOfDefencemenSinceFaceoff',
 'lastEventShotAngle',
 'ScoreDiff',
 'speedFromLastEvent',
 'defendingTeamAverageTimeOnIceOfDefencemenSinceFaceoff',
 'TOI',
 'ScoreSituation_down2',
 'TK',
 'Wrist_dist',
 'ShootingTeamSkaters',
 'Skater_Shots_rate',
 'Square_all',
 'Corsi_EV_CA',
 'shootingTeamMaxTimeOnIceOfDefencemenSinceFaceoff',
 'lastEventShotDistance',
 'shootingTeamAverageTimeOnIceOfForwardsSinceFaceoff',
 'defendingTeamMinTimeOnIceOfDefencemen',
 'Skater_Pts',
 'shootingTeamAverageTimeOnIce',
 'situation_5on4',
 'offWing',
 'defendingTeamMinTimeOnIceOfForwards',
 'Fenwick_EV_FF_PCT_rel',
 'xCordAd

In [89]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
0      0          8475299        Joni Ortio          8473548   
1      0          8475299        Joni Ortio          8473548   
9      0          8476899       Matt Murray          8473563   
12     0          8476899       Matt Murray          8473563   
13     0          8475660        Cam Talbot          8478562   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
0         Phil Kessel  201520970  0.048010    2015              0       3   
1         Phil Kessel  201520970  0.084865    2015              0       3   
9   Nicklas Backstrom  201530225  0.040731    2015              1       2   
12  Nicklas Backstrom  201530225  0.086180    2015              1       2   
13     Jakub Nakladal  201521176  0.004383    2015              0       2   

    xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
0              56             20          31.218403                   0.0   
1              82             12          59.743563                   0.0   
9              51            -23          31.184975                   0.0   
12             61            -11          21.447736                   0.0   
13             34            -19          19.057705                   0.0   

    shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
0                           0     38.587563            0   
1                           0     13.892444            0   
9                           0     44.418465            0   
12                          0     30.083218            0   
13                          0     58.189346            0   

    shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0                         0.0         0            1.307966   
1                         0.0         0            1.171516   
9                         0.0         0            1.046267   
12                        0.0         0            2.600000   
13                        0.0         0            0.950323   

    lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0                  0.0                    0.0                53   
1                  0.0                    0.0                70   
9                  0.0                    0.0                47   
12                 0.0                    0.0                10   
13                 0.0                    0.0                17   

    shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                             53                          5   
1                             14                          5   
9                             47                          4   
12                            10                          4   
13                            17                          3   

    shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                             1                          96.0   
1                             1                         113.0   
9                             1                          47.0   
12                            1                          18.0   
13                            2                          27.0   

    shootingTeamAverageTimeOnIceOfForwards  \
0                               104.600000   
1                               121.600000   
9                                47.000000   
12                               12.000000   
13                               25.333333   

    shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                       53.0                       122   
1                                       70.0                       139   
9                                       47.0                        47   
12                                      42.0                        42   
13                                      29.5                        42   

    shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTim

In [90]:
#randomly sample 10,000 rows
dfs = dftst.sample(100000, random_state=99)

In [91]:
dfs.head()

goal  goalieIdForShot  goalieNameForShot  shooterPlayerId  \
896280      0          8473503       James Reimer          8474161   
858216      0          8469514        Peter Budaj          8470642   
800773      0          8474651      Braden Holtby          8470616   
1004464     0          8470594  Marc-Andre Fleury          8470309   
460311      0          8470860     Jaroslav Halak          8475169   

           shooterName        uid     xGoal  season  isPlayoffGame  period  \
896280   Jakub Voracek  201620385  0.058278    2016              0       2   
858216      Shea Weber  201620377  0.005247    2016              0       4   
800773     Ryan Kesler  201621014  0.307963    2016              0       3   
1004464   Ryan Whitney  200920202  0.032204    2009              0       2   
460311    Evander Kane  201020149  0.555098    2010              0       3   

         xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
896280              64            -25          45.000000   
858216              43             16          19.179008   
800773              81              2          14.036243   
1004464             45             -6           7.765166   
460311              78            -16          55.491477   

         shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
896280                    0.0                          0     35.355339   
858216                    0.0                          0     48.703183   
800773                    0.0                          0      8.246211   
1004464                   0.0                          0     44.407207   
460311                    0.0                          0     19.416488   

         shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
896280             0                        0.0         0            3.938767   
858216             0                        0.0         0            1.905952   
800773             0                        0.0         0            3.605551   
1004464            0                        0.0         0            1.143959   
460311             0                        0.0         0            0.600925   

         lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
896280                  0.0                    0.0                12   
858216                  0.0                    0.0                59   
800773                  0.0                    0.0                27   
1004464                 0.0                    0.0                91   
460311                  0.0                    0.0                18   

         shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
896280                             12                          4   
858216                             14                          3   
800773                             27                          4   
1004464                            68                          3   
460311                             18                          4   

         shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
896280                             1                         12.00   
858216                             1                         27.75   
800773                             1                         59.80   
1004464                            2                         80.20   
460311                             1                         68.80   

         shootingTeamAverageTimeOnIceOfForwards  \
896280                                12.000000   
858216                                17.333333   
800773                                68.000000   
1004464                               55.666667   
460311                                27.750000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
896280                                       12.0                        12   
858216                                       59.0                        59   
800773             

In [92]:
#create x & y sets on the 10,000 samples
y_train = dfs.iloc[:,0]
X_train = dfs.iloc[:,8:]
X_train.shape

(100000, 197)

In [93]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  \
896280               0       2             64            -25   
858216               0       4             43             16   
800773               0       3             81              2   
1004464              0       2             45             -6   
460311               0       3             78            -16   

         shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
896280           45.000000                   0.0                          0   
858216           19.179008                   0.0                          0   
800773           14.036243                   0.0                          0   
1004464           7.765166                   0.0                          0   
460311           55.491477                   0.0                          0   

         shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
896280      35.355339            0                        0.0         0   
858216      48.703183            0                        0.0         0   
800773       8.246211            0                        0.0         0   
1004464     44.407207            0                        0.0         0   
460311      19.416488            0                        0.0         0   

         speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
896280             3.938767                 0.0                    0.0   
858216             1.905952                 0.0                    0.0   
800773             3.605551                 0.0                    0.0   
1004464            1.143959                 0.0                    0.0   
460311             0.600925                 0.0                    0.0   

         shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  \
896280                 12                            12   
858216                 59                            14   
800773                 27                            27   
1004464                91                            68   
460311                 18                            18   

         shootingTeamForwardsOnIce  shootingTeamDefencemenOnIce  \
896280                           4                            1   
858216                           3                            1   
800773                           4                            1   
1004464                          3                            2   
460311                           4                            1   

         shootingTeamAverageTimeOnIce  shootingTeamAverageTimeOnIceOfForwards  \
896280                          12.00                               12.000000   
858216                          27.75                               17.333333   
800773                          59.80                               68.000000   
1004464                         80.20                               55.666667   
460311                          68.80                               27.750000   

         shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
896280                                       12.0                        12   
858216                                       59.0                        59   
800773                                       27.0                       106   
1004464                                     117.0                       143   
460311                                      233.0                       233   

         shootingTeamMaxTimeOnIceOfForwards  \
896280                                   12   
858216                                   24   
800773                                  106   
1004464                                  76   
460311                                   57   

         shootingTeamMaxTimeOnIceOfDefencemen  shootingTeamMinTimeOnIce  \
896280                                     12                        12   
858216                                     59                        14   
800773                   

In [94]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dfnew.shape

(19694, 205)

In [95]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(19694, 197)

In [96]:
X1 = X_train[ndnew]
X1.shape

(100000, 62)

In [97]:
X1_test = X_test[ndnew]
X1_test.shape

(19694, 62)

**Create clusters and add to the dataset**

In [98]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)
#gaus = GaussianMixture(n_components=2, random_state=0).fit_predict(pca_rf)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


In [99]:
selector.shape

(100000, 67)

**XGBoost for hyperparameter tuning**

In [100]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16)

#set parmeter grid
params = {
        'min_child_weight': [10,20,30],
        'n_estimators': [5000,7500,9000],
        'learning_rate' : [0.001],
        'subsample': [0.5],
        'max_depth': [5,6,7,8]
        }

#create GridSearchCV object and fit it versus training data
grid = GridSearchCV(estimator=xgb, param_grid=params, scoring='neg_log_loss', n_jobs=-1, cv=5, verbose=10 )
grid.fit(selector, y_train)

#extract the best params from 'grid'
best_hyperparams = grid.best_params_
print(best_hyperparams)

#extract best CV score 
best_CV_score = grid.best_score_
print(best_CV_score)

#extract best model from grid
best_xg = grid.best_estimator_

#Fit the model to the data
best = best_xg.fit(selector,y_train)

#make predictions on test data
y_pred = best.predict(selector_test)
predictions = [round(value) for value in y_pred]

#create confusion & classification matrix
from sklearn.metrics import classification_report,confusion_matrix
print(confusion_matrix(y_test,predictions))
print(classification_report(y_test,predictions,digits=3))

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

Fitting 5 folds for each of 36 candidates, totalling 180 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 36 concurrent workers.
[Parallel(n_jobs=-1)]: Done  13 tasks      | elapsed:  8.8min
[Parallel(n_jobs=-1)]: Done  26 tasks      | elapsed: 13.5min
[Parallel(n_jobs=-1)]: Done  41 tasks      | elapsed: 19.2min
[Parallel(n_jobs=-1)]: Done  56 tasks      | elapsed: 25.9min
[Parallel(n_jobs=-1)]: Done  73 tasks      | elapsed: 31.4min
[Parallel(n_jobs=-1)]: Done  90 tasks      | elapsed: 39.8min
[Parallel(n_jobs=-1)]: Done 109 tasks      | elapsed: 49.1min
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/externals/joblib/externals/loky/process_executor.py:706: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  "timeout or by a memory leak.", UserWarning
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/externals/joblib/externals/loky/process_executor.py:706: UserWarning: A worker stopped while s

{'learning_rate': 0.001, 'max_depth': 5, 'min_child_weight': 10, 'n_estimators': 7500, 'subsample': 0.5}
-0.27430082873845474
[[17846    22]
 [ 1808    18]]
              precision    recall  f1-score   support

           0      0.908     0.999     0.951     17868
           1      0.450     0.010     0.019      1826

   micro avg      0.907     0.907     0.907     19694
   macro avg      0.679     0.504     0.485     19694
weighted avg      0.866     0.907     0.865     19694



array([0.01048337, 0.01157303, 0.00931916, 0.00834848, 0.00974089,
       0.08696555, 0.06093645, 0.0936361 , 0.04244862, 0.02047211,
       0.0265512 , 0.01409021, 0.01525092, 0.01421076, 0.01810872,
       0.01604421, 0.0133084 , 0.01214079, 0.01608076, 0.0107304 ,
       0.01429338, 0.00994043, 0.01135081, 0.00996708, 0.01134042,
       0.01136079, 0.01279585, 0.00945414, 0.00926831, 0.01054543,
       0.00969525, 0.01404095, 0.01343631, 0.00946991, 0.01638665,
       0.00959334, 0.01052075, 0.01146844, 0.00969092, 0.00953825,
       0.00947268, 0.01004442, 0.00957842, 0.00992416, 0.01168162,
       0.00936775, 0.01025411, 0.00947164, 0.00972153, 0.00972668,
       0.00996475, 0.01012822, 0.01119649, 0.00954983, 0.00972834,
       0.00969624, 0.00939732, 0.01099562, 0.00909611, 0.00965807,
       0.00965939, 0.00946678, 0.01006255, 0.00948847, 0.00918157,
       0.00918769, 0.00970189], dtype=float32)

In [104]:
predictions_prob = best.predict_proba(selector_test)

In [105]:
print(predictions_prob)

[[0.88437796 0.11562204]
 [0.95681685 0.04318317]
 [0.9153965  0.08460347]
 ...
 [0.95305717 0.04694283]
 [0.91640097 0.08359903]
 [0.9622482  0.03775176]]


In [106]:
print(log_loss(y_test,predictions_prob[:,1]))

0.28313681771839705


**XGBoost trained against all observations pre-2017**

In [107]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
0      0          8475299        Joni Ortio          8473548   
1      0          8475299        Joni Ortio          8473548   
9      0          8476899       Matt Murray          8473563   
12     0          8476899       Matt Murray          8473563   
13     0          8475660        Cam Talbot          8478562   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
0         Phil Kessel  201520970  0.048010    2015              0       3   
1         Phil Kessel  201520970  0.084865    2015              0       3   
9   Nicklas Backstrom  201530225  0.040731    2015              1       2   
12  Nicklas Backstrom  201530225  0.086180    2015              1       2   
13     Jakub Nakladal  201521176  0.004383    2015              0       2   

    xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
0              56             20          31.218403                   0.0   
1              82             12          59.743563                   0.0   
9              51            -23          31.184975                   0.0   
12             61            -11          21.447736                   0.0   
13             34            -19          19.057705                   0.0   

    shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
0                           0     38.587563            0   
1                           0     13.892444            0   
9                           0     44.418465            0   
12                          0     30.083218            0   
13                          0     58.189346            0   

    shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0                         0.0         0            1.307966   
1                         0.0         0            1.171516   
9                         0.0         0            1.046267   
12                        0.0         0            2.600000   
13                        0.0         0            0.950323   

    lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0                  0.0                    0.0                53   
1                  0.0                    0.0                70   
9                  0.0                    0.0                47   
12                 0.0                    0.0                10   
13                 0.0                    0.0                17   

    shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                             53                          5   
1                             14                          5   
9                             47                          4   
12                            10                          4   
13                            17                          3   

    shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                             1                          96.0   
1                             1                         113.0   
9                             1                          47.0   
12                            1                          18.0   
13                            2                          27.0   

    shootingTeamAverageTimeOnIceOfForwards  \
0                               104.600000   
1                               121.600000   
9                                47.000000   
12                               12.000000   
13                               25.333333   

    shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                       53.0                       122   
1                                       70.0                       139   
9                                       47.0                        47   
12                                      42.0                        42   
13                                      29.5                        42   

    shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTim

In [108]:
#create x & y sets on the 10,000 samples
y_train = dftst.iloc[:,0]
X_train = dftst.iloc[:,8:]
X_train.shape

(144050, 197)

In [109]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
0               0       3             56             20          31.218403   
1               0       3             82             12          59.743563   
9               1       2             51            -23          31.184975   
12              1       2             61            -11          21.447736   
13              0       2             34            -19          19.057705   

    shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
0                    0.0                          0     38.587563   
1                    0.0                          0     13.892444   
9                    0.0                          0     44.418465   
12                   0.0                          0     30.083218   
13                   0.0                          0     58.189346   

    shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0             0                        0.0         0            1.307966   
1             0                        0.0         0            1.171516   
9             0                        0.0         0            1.046267   
12            0                        0.0         0            2.600000   
13            0                        0.0         0            0.950323   

    lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0                  0.0                    0.0                53   
1                  0.0                    0.0                70   
9                  0.0                    0.0                47   
12                 0.0                    0.0                10   
13                 0.0                    0.0                17   

    shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                             53                          5   
1                             14                          5   
9                             47                          4   
12                            10                          4   
13                            17                          3   

    shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                             1                          96.0   
1                             1                         113.0   
9                             1                          47.0   
12                            1                          18.0   
13                            2                          27.0   

    shootingTeamAverageTimeOnIceOfForwards  \
0                               104.600000   
1                               121.600000   
9                                47.000000   
12                               12.000000   
13                               25.333333   

    shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                       53.0                       122   
1                                       70.0                       139   
9                                       47.0                        47   
12                                      42.0                        42   
13                                      29.5                        42   

    shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
0                                  122                                    53   
1                                  139                                    70   
9                                   47                                    47   
12                                  14                                    42   
13                                  42                                    42   

    shootingTeamMinTimeOnIce  shootingTeamMinTimeOnIceOfForwards  \
0                         53                                  53   
1                         70                                  70   
9                         47                                  47   
12             

In [111]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dfnew.shape

(19694, 205)

In [112]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(19694, 197)

In [113]:
X1 = X_train[ndnew]
X1.shape

(144050, 62)

In [114]:
X1_test = X_test[ndnew]
X1_test.shape

(19694, 62)

In [115]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)
selector.ndim


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


2

In [116]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=32,
                    min_child_weight= 8,
                    n_estimators= 7500,
                    learning_rate = 0.001,
                    subsample= 0.6,
                    max_depth= 5
                   )

best = xgb.fit(selector, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

array([0.00967075, 0.00984724, 0.00865589, 0.00768527, 0.0082409 ,
       0.11412387, 0.03891472, 0.16370407, 0.        , 0.01950072,
       0.03736688, 0.01587242, 0.01775872, 0.01577808, 0.01999362,
       0.01711914, 0.01272059, 0.01257453, 0.01472667, 0.01073629,
       0.01568142, 0.0092226 , 0.01157738, 0.01014091, 0.01154183,
       0.01046975, 0.01258458, 0.00883092, 0.00847943, 0.00922311,
       0.00835987, 0.01396946, 0.01441079, 0.00815902, 0.        ,
       0.00840572, 0.00969785, 0.0106568 , 0.00920113, 0.00861966,
       0.00900466, 0.00953029, 0.00839307, 0.01096563, 0.00953294,
       0.00881082, 0.00991216, 0.00846959, 0.0095143 , 0.00879283,
       0.00876295, 0.00969564, 0.01073681, 0.00876272, 0.00893825,
       0.00902952, 0.00836725, 0.01053359, 0.00825709, 0.00859897,
       0.00875786, 0.00937717, 0.00889901, 0.00833826, 0.00876752,
       0.00885511, 0.00817339], dtype=float32)

In [117]:
predictions_prob = best.predict_proba(selector_test)
print(log_loss(y_test,predictions_prob[:,1]))

0.2829042429763571


***Now Estimate All Power Play Shots Using the Final Model***

In [118]:
#create test set based on shots before 2017-18
dfpp = df[((df['situation_5on4'] == 1) | (df['situation_4on3'] == 1) | (df['situation_5on3'] == 1) | (df['situation_6on4'] == 1) | (df['situation_6on5'] == 1))]
dfpp.shape

(225961, 205)

In [119]:
#create x & y sets on the 10,000 samples
y_test = dfpp.iloc[:,0]
X_test = dfpp.iloc[:,8:]
X_test.shape

(225961, 197)

In [120]:
X1 = X_test[ndnew]
X1.shape

(225961, 62)

In [121]:
pca_r = pca_rf.transform(X1)
gaus_pc = gaus_pcarfe.predict(pca_r)
C = gaus_pc.reshape(-1, 1)
B = A.transform(C)
selector_final = np.concatenate((B, X1), axis=1)
selector_final.ndim

2

In [122]:
predictions_prob = best.predict_proba(selector_final)
print(log_loss(y_test,predictions_prob[:,1]))

0.27422615842754844


In [123]:
dfpp['xGoal_GT'] = predictions_prob[:,1]
dfpp.head()

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
0      0          8475299        Joni Ortio          8473548   
1      0          8475299        Joni Ortio          8473548   
9      0          8476899       Matt Murray          8473563   
12     0          8476899       Matt Murray          8473563   
13     0          8475660        Cam Talbot          8478562   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
0         Phil Kessel  201520970  0.048010    2015              0       3   
1         Phil Kessel  201520970  0.084865    2015              0       3   
9   Nicklas Backstrom  201530225  0.040731    2015              1       2   
12  Nicklas Backstrom  201530225  0.086180    2015              1       2   
13     Jakub Nakladal  201521176  0.004383    2015              0       2   

    xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
0              56             20          31.218403                   0.0   
1              82             12          59.743563                   0.0   
9              51            -23          31.184975                   0.0   
12             61            -11          21.447736                   0.0   
13             34            -19          19.057705                   0.0   

    shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
0                           0     38.587563            0   
1                           0     13.892444            0   
9                           0     44.418465            0   
12                          0     30.083218            0   
13                          0     58.189346            0   

    shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
0                         0.0         0            1.307966   
1                         0.0         0            1.171516   
9                         0.0         0            1.046267   
12                        0.0         0            2.600000   
13                        0.0         0            0.950323   

    lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
0                  0.0                    0.0                53   
1                  0.0                    0.0                70   
9                  0.0                    0.0                47   
12                 0.0                    0.0                10   
13                 0.0                    0.0                17   

    shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
0                             53                          5   
1                             14                          5   
9                             47                          4   
12                            10                          4   
13                            17                          3   

    shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
0                             1                          96.0   
1                             1                         113.0   
9                             1                          47.0   
12                            1                          18.0   
13                            2                          27.0   

    shootingTeamAverageTimeOnIceOfForwards  \
0                               104.600000   
1                               121.600000   
9                                47.000000   
12                               12.000000   
13                               25.333333   

    shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
0                                       53.0                       122   
1                                       70.0                       139   
9                                       47.0                        47   
12                                      42.0                        42   
13                                      29.5                        42   

    shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTim

****Short Handed****
_____________________________________

**Create a Random Sample**

In [124]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
2       0          8475660        Cam Talbot          8477591   
24      0          8471715    Ondrej Pavelec          8473533   
139     0          8476999     Linus Ullmark          8472410   
145     0          8475831  Philipp Grubauer          8470606   
151     0          8473461       Steve Mason          8476448   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
2         Josh Jooris  201521176  0.124527    2015              0       1   
24       Jordan Staal  201520849  0.113767    2015              0       1   
139    Stephen Gionta  201520107  0.049965    2015              0       3   
145      Dustin Brown  201520848  0.173571    2015              0       1   
151  William Karlsson  201520976  0.137988    2015              0       2   

     xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
2               63             13          26.565051             26.565051   
24              57              2           3.576334              0.000000   
139             80            -16          60.642246             60.642246   
145             77              8          33.690068              0.000000   
151             84             -6          50.194429              0.000000   

     shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
2                            0     29.068884            0   
24                           0     32.062439            0   
139                          0     18.357560            0   
145                          0     14.422205            0   
151                          0      7.810250            0   

     shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2                     8.855017         1           45.593616   
24                    0.000000         0           34.091788   
139                   2.332394         0            6.397346   
145                   0.000000         0           23.410586   
151                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     

In [125]:
#randomly sample 10,000 rows
dfs = dftst.sample(15000, random_state=99)

In [126]:
dfs.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
398783     0          8455710    Martin Brodeur          8474564   
42339      0          8475660        Cam Talbot          8470834   
491800     0          8471469       Pekka Rinne          8473446   
322691     0          8470645    Corey Crawford          8469492   
197295     0          8471403        Karri Ramo          8474590   

             shooterName        uid     xGoal  season  isPlayoffGame  period  \
398783    Steven Stamkos  201120280  0.080477    2011              0       2   
42339   Dustin Byfuglien  201520506  0.001000    2015              0       3   
491800      Erik Johnson  201021157  0.010616    2010              0       2   
322691      Fedor Tyutin  201220059  0.079379    2012              0       2   
197295      John Carlson  201320165  0.001000    2013              0       3   

        xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
398783             66            -11          25.559965              0.000000   
42339              79             14          54.462322              0.000000   
491800             73            -29          61.113418            125.650073   
322691             77             -1           4.763642             27.241742   
197295             88             10          84.289407              0.000000   

        shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
398783                          0     25.495098            0   
42339                           0     17.204651            0   
491800                          1     33.120990            0   
322691                          0     12.041595            0   
197295                          0     10.049876            0   

        shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
398783                   0.000000         0            0.720350   
42339                    0.000000         0            1.009151   
491800                  13.961119         0            5.595413   
322691                   3.405218         0            0.707107   
197295                   0.000000         0            5.390846   

        lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
398783            0.000000               0.000000                 4   
42339             0.000000               0.000000                41   
491800           64.536655              23.259407                10   
322691          -32.005383               9.433981                36   
197295            0.000000               0.000000                 7   

        shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
398783                             4                          3   
42339                             41                          2   
491800                            10                          2   
322691                            36                          2   
197295                             7                          2   

        shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
398783                            1                         24.25   
42339                             2                         27.50   
491800                            2                         18.00   
322691                            2                         36.00   
197295                            2                          7.00   

        shootingTeamAverageTimeOnIceOfForwards  \
398783                               29.333333   
42339                                14.000000   
491800                               26.000000   
322691                               36.000000   
197295                                7.000000   

        shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
398783                                       9.0                        69   
42339                                       41.0                        41   
491800                                      10.0               

In [127]:
#create x & y sets on the 10,000 samples
y_train = dfs.iloc[:,0]
X_train = dfs.iloc[:,8:]
X_train.shape

(15000, 197)

In [128]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  \
398783              0       2             66            -11   
42339               0       3             79             14   
491800              0       2             73            -29   
322691              0       2             77             -1   
197295              0       3             88             10   

        shotAngleAdjusted  shotAnglePlusRebound  shotAngleReboundRoyalRoad  \
398783          25.559965              0.000000                          0   
42339           54.462322              0.000000                          0   
491800          61.113418            125.650073                          1   
322691           4.763642             27.241742                          0   
197295          84.289407              0.000000                          0   

        shotDistance  shotRebound  shotAnglePlusReboundSpeed  shotRush  \
398783     25.495098            0                   0.000000         0   
42339      17.204651            0                   0.000000         0   
491800     33.120990            0                  13.961119         0   
322691     12.041595            0                   3.405218         0   
197295     10.049876            0                   0.000000         0   

        speedFromLastEvent  lastEventShotAngle  lastEventShotDistance  \
398783            0.720350            0.000000               0.000000   
42339             1.009151            0.000000               0.000000   
491800            5.595413           64.536655              23.259407   
322691            0.707107          -32.005383               9.433981   
197295            5.390846            0.000000               0.000000   

        shooterTimeOnIce  shooterTimeOnIceSinceFaceoff  \
398783                 4                             4   
42339                 41                            41   
491800                10                            10   
322691                36                            36   
197295                 7                             7   

        shootingTeamForwardsOnIce  shootingTeamDefencemenOnIce  \
398783                          3                            1   
42339                           2                            2   
491800                          2                            2   
322691                          2                            2   
197295                          2                            2   

        shootingTeamAverageTimeOnIce  shootingTeamAverageTimeOnIceOfForwards  \
398783                         24.25                               29.333333   
42339                          27.50                               14.000000   
491800                         18.00                               26.000000   
322691                         36.00                               36.000000   
197295                          7.00                                7.000000   

        shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
398783                                       9.0                        69   
42339                                       41.0                        41   
491800                                      10.0                        42   
322691                                      36.0                        36   
197295                                       7.0                         7   

        shootingTeamMaxTimeOnIceOfForwards  \
398783                                  69   
42339                                   19   
491800                                  42   
322691                                  36   
197295                                   7   

        shootingTeamMaxTimeOnIceOfDefencemen  shootingTeamMinTimeOnIce  \
398783                                     9                         4   
42339                                     41                         9   
491800                                    10                        10   
322691 

In [129]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dfnew.shape

(2745, 205)

In [130]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(2745, 197)

**XGBoost for feature selection**

In [131]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16,
                    min_child_weight= 8,
                    n_estimators= 7500,
                    learning_rate = 0.001,
                    subsample= 0.8,
                    max_depth= 6
                   )

best = xgb.fit(X_train, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
both = zip(list(best.feature_importances_),X_train.columns)
ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
ndf.sort_values('Importance',ascending=False,inplace=True)
print(ndf)

     Importance                                            Feature
57     0.039855                          arenaAdjustedShotDistance
77     0.022754                                        Square_dist
60     0.016659                              arenaAdjustedYCordAbs
79     0.015867                                         Square_all
7      0.012964                                       shotDistance
75     0.008496                                         Dist_angle
8      0.008272                                        shotRebound
70     0.007682                                          Back_dist
92     0.007512                                      shotType_SNAP
11     0.007469                                 speedFromLastEvent
71     0.007375                                         Quick_dist
33     0.007059               shootingTeamMinTimeOnIceSinceFaceoff
4      0.007022                                  shotAngleAdjusted
76     0.006770                                       Rebound_

In [140]:
ndnew = ndf['Feature'][ndf['Importance'] > 0.00577].tolist()
ndnew

['arenaAdjustedShotDistance',
 'Square_dist',
 'arenaAdjustedYCordAbs',
 'Square_all',
 'shotDistance',
 'Dist_angle',
 'shotRebound',
 'Back_dist',
 'shotType_SNAP',
 'speedFromLastEvent',
 'Quick_dist',
 'shootingTeamMinTimeOnIceSinceFaceoff',
 'shotAngleAdjusted',
 'Rebound_dist',
 'shootingTeamMinTimeOnIce',
 'Skater_Pts',
 'lastEventShotAngle',
 'shootingTeamMinTimeOnIceOfDefencemenSinceFaceoff',
 'shotType_SLAP',
 'defendingTeamMaxTimeOnIceOfDefencemen',
 'shootingTeamMinTimeOnIceOfForwards',
 'xCordAdjusted',
 'Skater_EV_G',
 'shootingTeamMaxTimeOnIceOfForwardsSinceFaceoff',
 'shotType_BACK',
 'defendingTeamMinTimeOnIceOfDefencemenSinceFaceoff',
 'FOL',
 'defendingTeamMinTimeOnIceOfForwards',
 'ScoreSituation_up1',
 'shootingTeamMinTimeOnIceOfDefencemen',
 'ATOI',
 'FOL_rate',
 'TK',
 'timeDifferenceSinceChange',
 'offWing',
 'shootingTeamAverageTimeOnIceOfForwards',
 'Corsi_EV_CA',
 'defendingTeamMaxTimeOnIceOfForwards',
 'shootingTeamAverageTimeOnIceOfForwardsSinceFaceoff',
 '

In [141]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
2       0          8475660        Cam Talbot          8477591   
24      0          8471715    Ondrej Pavelec          8473533   
139     0          8476999     Linus Ullmark          8472410   
145     0          8475831  Philipp Grubauer          8470606   
151     0          8473461       Steve Mason          8476448   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
2         Josh Jooris  201521176  0.124527    2015              0       1   
24       Jordan Staal  201520849  0.113767    2015              0       1   
139    Stephen Gionta  201520107  0.049965    2015              0       3   
145      Dustin Brown  201520848  0.173571    2015              0       1   
151  William Karlsson  201520976  0.137988    2015              0       2   

     xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
2               63             13          26.565051             26.565051   
24              57              2           3.576334              0.000000   
139             80            -16          60.642246             60.642246   
145             77              8          33.690068              0.000000   
151             84             -6          50.194429              0.000000   

     shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
2                            0     29.068884            0   
24                           0     32.062439            0   
139                          0     18.357560            0   
145                          0     14.422205            0   
151                          0      7.810250            0   

     shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2                     8.855017         1           45.593616   
24                    0.000000         0           34.091788   
139                   2.332394         0            6.397346   
145                   0.000000         0           23.410586   
151                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     

In [142]:
#create x & y sets on the 10,000 samples
y_train = dftst.iloc[:,0]
X_train = dftst.iloc[:,8:]
X_train.shape

(18225, 197)

In [143]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
2                0       1             63             13          26.565051   
24               0       1             57              2           3.576334   
139              0       3             80            -16          60.642246   
145              0       1             77              8          33.690068   
151              0       2             84             -6          50.194429   

     shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
2               26.565051                          0     29.068884   
24               0.000000                          0     32.062439   
139             60.642246                          0     18.357560   
145              0.000000                          0     14.422205   
151              0.000000                          0      7.810250   

     shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2              0                   8.855017         1           45.593616   
24             0                   0.000000         0           34.091788   
139            0                   2.332394         0            6.397346   
145            0                   0.000000         0           23.410586   
151            0                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
2                                    15                                    15   
24                                   45                                     2   
139                                  26                                    22   
145                                  65                                    16   
151                                  36                                    72   

     shootingTeamMinTimeOnIce  shootingTeamMinTimeOnIceOfForwards  \
2                           1                                   1   
24                          2                                  45   
139                        

In [144]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dfnew.shape

(2745, 205)

In [145]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(2745, 197)

In [146]:
X1 = X_train[ndnew]
X1.shape

(18225, 63)

In [147]:
X1_test = X_test[ndnew]
X1_test.shape

(2745, 63)

**Create clusters and add to the dataset**

In [148]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)
#gaus = GaussianMixture(n_components=2, random_state=0).fit_predict(pca_rf)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


In [149]:
selector.shape

(18225, 68)

**XGBoost for parameter tuning**

In [150]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=16)

#set parmeter grid
params = {
        'min_child_weight': [2,5,8,10,15],
        'n_estimators': [2000,6000,7500,8500,10000],
        'learning_rate' : [0.001,0.01,0.0001],
        'subsample': [0.5,0.75],
        'max_depth': [5,6,7,8,9]
        }

#create GridSearchCV object and fit it versus training data
grid = GridSearchCV(estimator=xgb, param_grid=params, scoring='neg_log_loss', n_jobs=-1, cv=5, verbose=10 )
grid.fit(selector, y_train)

#extract the best params from 'grid'
best_hyperparams = grid.best_params_
print(best_hyperparams)

#extract best CV score 
best_CV_score = grid.best_score_
print(best_CV_score)

#extract best model from grid
best_xg = grid.best_estimator_

#Fit the model to the data
best = best_xg.fit(selector,y_train)

#make predictions on test data
y_pred = best.predict(selector_test)
predictions = [round(value) for value in y_pred]

#create confusion & classification matrix
from sklearn.metrics import classification_report,confusion_matrix
print(confusion_matrix(y_test,predictions))
print(classification_report(y_test,predictions,digits=3))

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

Fitting 5 folds for each of 750 candidates, totalling 3750 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 36 concurrent workers.
[Parallel(n_jobs=-1)]: Done  13 tasks      | elapsed:  2.1min
[Parallel(n_jobs=-1)]: Done  26 tasks      | elapsed:  2.7min
[Parallel(n_jobs=-1)]: Done  41 tasks      | elapsed:  3.0min
[Parallel(n_jobs=-1)]: Done  56 tasks      | elapsed:  4.2min
[Parallel(n_jobs=-1)]: Done  73 tasks      | elapsed:  5.5min
[Parallel(n_jobs=-1)]: Done  90 tasks      | elapsed:  6.1min
[Parallel(n_jobs=-1)]: Done 109 tasks      | elapsed:  8.0min
[Parallel(n_jobs=-1)]: Done 128 tasks      | elapsed:  8.7min
[Parallel(n_jobs=-1)]: Done 149 tasks      | elapsed: 10.5min
[Parallel(n_jobs=-1)]: Done 170 tasks      | elapsed: 11.6min
[Parallel(n_jobs=-1)]: Done 193 tasks      | elapsed: 13.0min
[Parallel(n_jobs=-1)]: Done 216 tasks      | elapsed: 14.6min
[Parallel(n_jobs=-1)]: Done 241 tasks      | elapsed: 15.9min
[Parallel(n_jobs=-1)]: Done 266 tasks      | elapsed: 17.8min
[Parallel(n_jobs=-1)]: Done 293 tasks      | elapsed: 1

{'learning_rate': 0.001, 'max_depth': 5, 'min_child_weight': 8, 'n_estimators': 7500, 'subsample': 0.75}
-0.22218935822102207
[[2545    2]
 [ 197    1]]
              precision    recall  f1-score   support

           0      0.928     0.999     0.962      2547
           1      0.333     0.005     0.010       198

   micro avg      0.928     0.928     0.928      2745
   macro avg      0.631     0.502     0.486      2745
weighted avg      0.885     0.928     0.894      2745



array([0.00950847, 0.00835219, 0.00568594, 0.0103211 , 0.01315839,
       0.08733176, 0.04536293, 0.04322858, 0.03058125, 0.0282012 ,
       0.01973815, 0.01717133, 0.01614689, 0.0123892 , 0.01499343,
       0.01545814, 0.0149989 , 0.0146816 , 0.01507433, 0.01392561,
       0.01149509, 0.01024587, 0.01438142, 0.00866676, 0.01266911,
       0.01293229, 0.01329545, 0.01311346, 0.01128486, 0.01428078,
       0.01073866, 0.01169971, 0.01082205, 0.01375455, 0.01235146,
       0.01141484, 0.01166267, 0.01072105, 0.01259185, 0.01272595,
       0.0125641 , 0.01046039, 0.01245366, 0.01214533, 0.01063611,
       0.01284388, 0.01100288, 0.01192136, 0.01219181, 0.01156048,
       0.0133907 , 0.01187227, 0.01145392, 0.01044864, 0.01159472,
       0.01147181, 0.01039551, 0.01103221, 0.01100644, 0.01264274,
       0.0120824 , 0.01109533, 0.01144007, 0.01050065, 0.01208676,
       0.0118099 , 0.00992301, 0.01081561], dtype=float32)

In [151]:
predictions_prob = best.predict_proba(selector_test)

In [152]:
print(predictions_prob)

[[0.9934499  0.0065501 ]
 [0.9835418  0.01645821]
 [0.96697754 0.03302246]
 ...
 [0.9795681  0.0204319 ]
 [0.9793358  0.02066424]
 [0.63889706 0.36110297]]


In [153]:
print(log_loss(y_test,predictions_prob[:,1]))

0.21120503387245976


**XGBoost trained against all observations pre-2017**

In [154]:
#create training set based on shots before 2017-18
dftst = df[((df['season'] < 2017) & (df['season'] > 2008)) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dftst.head()

goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
2       0          8475660        Cam Talbot          8477591   
24      0          8471715    Ondrej Pavelec          8473533   
139     0          8476999     Linus Ullmark          8472410   
145     0          8475831  Philipp Grubauer          8470606   
151     0          8473461       Steve Mason          8476448   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
2         Josh Jooris  201521176  0.124527    2015              0       1   
24       Jordan Staal  201520849  0.113767    2015              0       1   
139    Stephen Gionta  201520107  0.049965    2015              0       3   
145      Dustin Brown  201520848  0.173571    2015              0       1   
151  William Karlsson  201520976  0.137988    2015              0       2   

     xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
2               63             13          26.565051             26.565051   
24              57              2           3.576334              0.000000   
139             80            -16          60.642246             60.642246   
145             77              8          33.690068              0.000000   
151             84             -6          50.194429              0.000000   

     shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
2                            0     29.068884            0   
24                           0     32.062439            0   
139                          0     18.357560            0   
145                          0     14.422205            0   
151                          0      7.810250            0   

     shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2                     8.855017         1           45.593616   
24                    0.000000         0           34.091788   
139                   2.332394         0            6.397346   
145                   0.000000         0           23.410586   
151                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     

In [155]:
#create x & y sets on the 10,000 samples
y_train = dftst.iloc[:,0]
X_train = dftst.iloc[:,8:]
X_train.shape

(18225, 197)

In [156]:
X_train.head()

isPlayoffGame  period  xCordAdjusted  yCordAdjusted  shotAngleAdjusted  \
2                0       1             63             13          26.565051   
24               0       1             57              2           3.576334   
139              0       3             80            -16          60.642246   
145              0       1             77              8          33.690068   
151              0       2             84             -6          50.194429   

     shotAnglePlusRebound  shotAngleReboundRoyalRoad  shotDistance  \
2               26.565051                          0     29.068884   
24               0.000000                          0     32.062439   
139             60.642246                          0     18.357560   
145              0.000000                          0     14.422205   
151              0.000000                          0      7.810250   

     shotRebound  shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2              0                   8.855017         1           45.593616   
24             0                   0.000000         0           34.091788   
139            0                   2.332394         0            6.397346   
145            0                   0.000000         0           23.410586   
151            0                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     shootingTeamMaxTimeOnIceOfForwards  shootingTeamMaxTimeOnIceOfDefencemen  \
2                                    15                                    15   
24                                   45                                     2   
139                                  26                                    22   
145                                  65                                    16   
151                                  36                                    72   

     shootingTeamMinTimeOnIce  shootingTeamMinTimeOnIceOfForwards  \
2                           1                                   1   
24                          2                                  45   
139                        

In [157]:
#create test set based on shots before 2017-18
dfnew = df[(df['season'] == 2017) & ((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dfnew.shape

(2745, 205)

In [158]:
#create x & y sets on the 10,000 samples
y_test = dfnew.iloc[:,0]
X_test = dfnew.iloc[:,8:]
X_test.shape

(2745, 197)

In [159]:
X1 = X_train[ndnew]
X1.shape

(18225, 63)

In [160]:
X1_test = X_test[ndnew]
X1_test.shape

(2745, 63)

In [161]:
y = df.iloc[:,0]
pca = PCA(n_components=8)
pca_rf = pca.fit(X1)
pca_r = pca_rf.transform(X1)
pcar = pca_rf.transform(X1_test)

gaus_pcarfe = GaussianMixture(n_components=5, random_state=0).fit(pca_r)
gaus_pc = gaus_pcarfe.predict(pca_r)
gaus = gaus_pcarfe.predict(pcar)

C = gaus_pc.reshape(-1, 1)
C2 = gaus.reshape(-1, 1)
onehot_encoder = OneHotEncoder(sparse=False)
A = onehot_encoder.fit(C)
B = A.transform(C)
B2 = A.transform(C2)
selector = np.concatenate((B, X1), axis=1)
selector_test  = np.concatenate((B2, X1_test), axis=1)
selector.ndim


/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/sklearn/preprocessing/_encoders.py:371: FutureWarning: The handling of integer data will change in version 0.22. Currently, the categories are determined based on the range [0, max(values)], while in the future they will be determined based on the unique values.
If you want the future behaviour and silence this warning, you can specify "categories='auto'".
In case you used a LabelEncoder before this OneHotEncoder to convert the categories to integers, then you can now use the OneHotEncoder directly.
  warnings.warn(msg, FutureWarning)


2

In [162]:
#XGBoost -------------------------------------------------------------------------------------------------
from xgboost import XGBClassifier

# fit model no training data
xgb = XGBClassifier(objective='binary:logistic',
                    silent=True, seed=99, tree_method='hist',max_bin=64,
                    min_child_weight= 8,
                    n_estimators= 7750,
                    learning_rate = 0.001,
                    subsample= 0.95,
                    max_depth= 5
                   )

best = xgb.fit(selector, y_train)

#extract the most imporatant features for xgboost
best.feature_importances_
#both = zip(list(best.feature_importances_),X_train.columns)
#ndf = pd.DataFrame(list(both), columns=['Importance', 'Feature'])
#ndf.sort_values('Importance',ascending=False,inplace=True)
#print(ndf)

array([0.01025622, 0.0095683 , 0.0050939 , 0.01135751, 0.01101735,
       0.08183602, 0.05263721, 0.04600159, 0.027313  , 0.        ,
       0.        , 0.01833903, 0.01759269, 0.01373837, 0.01536844,
       0.01716432, 0.01837819, 0.01461587, 0.01603195, 0.01677425,
       0.01117195, 0.01077298, 0.01403515, 0.0067839 , 0.01358857,
       0.01333533, 0.01431699, 0.01583012, 0.01420956, 0.01347722,
       0.01145097, 0.01138693, 0.01149042, 0.01773947, 0.01420669,
       0.01286583, 0.01202121, 0.01050816, 0.01446949, 0.01587427,
       0.01380615, 0.01087794, 0.01139388, 0.01280251, 0.01094563,
       0.01190748, 0.01304117, 0.        , 0.01416728, 0.01196225,
       0.01600042, 0.01212167, 0.01365383, 0.01145817, 0.01246575,
       0.01392472, 0.01157499, 0.01280104, 0.01174893, 0.01286644,
       0.014906  , 0.01252259, 0.01222687, 0.01204763, 0.01261288,
       0.01340824, 0.01005906, 0.01007707], dtype=float32)

In [163]:
predictions_prob = best.predict_proba(selector_test)
print(log_loss(y_test,predictions_prob[:,1]))

0.21094417831587362


***Now Estimate All Short Handed Shots Using the Final Model***

In [164]:
#create test set based on shots before 2017-18
dfsh = df[((df['situation_4on5'] == 1) | (df['situation_3on4'] == 1) | (df['situation_3on5'] == 1))]
dfsh.shape

(29880, 205)

In [165]:
#create x & y sets on the 10,000 samples
y_test = dfsh.iloc[:,0]
X_test = dfsh.iloc[:,8:]
X_test.shape

(29880, 197)

In [166]:
X1 = X_test[ndnew]
X1.shape

(29880, 63)

In [167]:
pca_r = pca_rf.transform(X1)
gaus_pc = gaus_pcarfe.predict(pca_r)
C = gaus_pc.reshape(-1, 1)
B = A.transform(C)
selector_final = np.concatenate((B, X1), axis=1)
selector_final.ndim

2

In [168]:
predictions_prob = best.predict_proba(selector_final)
print(log_loss(y_test,predictions_prob[:,1]))

0.20105724805457034


In [169]:
dfsh['xGoal_GT'] = predictions_prob[:,1]
dfsh.head()

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


goal  goalieIdForShot goalieNameForShot  shooterPlayerId  \
2       0          8475660        Cam Talbot          8477591   
24      0          8471715    Ondrej Pavelec          8473533   
139     0          8476999     Linus Ullmark          8472410   
145     0          8475831  Philipp Grubauer          8470606   
151     0          8473461       Steve Mason          8476448   

          shooterName        uid     xGoal  season  isPlayoffGame  period  \
2         Josh Jooris  201521176  0.124527    2015              0       1   
24       Jordan Staal  201520849  0.113767    2015              0       1   
139    Stephen Gionta  201520107  0.049965    2015              0       3   
145      Dustin Brown  201520848  0.173571    2015              0       1   
151  William Karlsson  201520976  0.137988    2015              0       2   

     xCordAdjusted  yCordAdjusted  shotAngleAdjusted  shotAnglePlusRebound  \
2               63             13          26.565051             26.565051   
24              57              2           3.576334              0.000000   
139             80            -16          60.642246             60.642246   
145             77              8          33.690068              0.000000   
151             84             -6          50.194429              0.000000   

     shotAngleReboundRoyalRoad  shotDistance  shotRebound  \
2                            0     29.068884            0   
24                           0     32.062439            0   
139                          0     18.357560            0   
145                          0     14.422205            0   
151                          0      7.810250            0   

     shotAnglePlusReboundSpeed  shotRush  speedFromLastEvent  \
2                     8.855017         1           45.593616   
24                    0.000000         0           34.091788   
139                   2.332394         0            6.397346   
145                   0.000000         0           23.410586   
151                   0.000000         0            6.250799   

     lastEventShotAngle  lastEventShotDistance  shooterTimeOnIce  \
2                   0.0                    0.0                15   
24                  0.0                    0.0                45   
139                 0.0                    0.0                26   
145                 0.0                    0.0                65   
151                 0.0                    0.0                36   

     shooterTimeOnIceSinceFaceoff  shootingTeamForwardsOnIce  \
2                              15                          2   
24                             45                          2   
139                            26                          2   
145                            16                          2   
151                            36                          2   

     shootingTeamDefencemenOnIce  shootingTeamAverageTimeOnIce  \
2                              2                         11.50   
24                             2                         23.50   
139                            2                         22.25   
145                            2                         28.25   
151                            2                         54.00   

     shootingTeamAverageTimeOnIceOfForwards  \
2                                       8.0   
24                                     45.0   
139                                    22.5   
145                                    40.5   
151                                    36.0   

     shootingTeamAverageTimeOnIceOfDefencemen  shootingTeamMaxTimeOnIce  \
2                                        15.0                        15   
24                                        2.0                        45   
139                                      22.0                        26   
145                                      16.0                        65   
151                                      72.0                        72   

     

**Join the three tables together to create final df**

In [170]:
df_all_rows = pd.concat([dffinal, dfpp, dfsh])
df_all_rows

goal  goalieIdForShot   goalieNameForShot  shooterPlayerId  \
3           0          8475299          Joni Ortio          8474034   
4           0          8475299          Joni Ortio          8471816   
5           0          8475299          Joni Ortio          8474034   
6           0          8475660          Cam Talbot          8474577   
7           0          8475660          Cam Talbot          8474673   
8           0          8474651       Braden Holtby          8473548   
10          0          8476899         Matt Murray          8473563   
11          0          8474651       Braden Holtby          8474602   
14          1          8475660          Cam Talbot          8474577   
15          0          8475660          Cam Talbot          8477445   
16          0          8475299          Joni Ortio          8474034   
17          0          8475660          Cam Talbot          8474673   
18          0          8474651       Braden Holtby          8474602   
19          0          8474651       Braden Holtby          8474602   
20          0          8474651       Braden Holtby          8473548   
23          0          8471715      Ondrej Pavelec          8473533   
26          0          8471715      Ondrej Pavelec          8476858   
28          0          8471695         Tuukka Rask          8475191   
29          0          8471219          Al Montoya          8476792   
30          0          8471695         Tuukka Rask          8475191   
31          0          8471695         Tuukka Rask          8475191   
32          0          8473575     Semyon Varlamov          8476441   
33          0          8476883  Andrei Vasilevskiy          8475798   
34          0          8476883  Andrei Vasilevskiy          8475798   
35          1          8471239      Cory Schneider          8475763   
36          0          8468685    Henrik Lundqvist          8475185   
37          0          8468685    Henrik Lundqvist          8472410   
38          0          8468685    Henrik Lundqvist          8475185   
39          0          8471239      Cory Schneider          8467096   
40          0          8468685    Henrik Lundqvist          8475185   
...       ...              ...                 ...              ...   
1253144     0          8462047        Martin Biron          8467466   
1253156     0          8469732      Joey MacDonald          8467346   
1253222     0          8473972        Jonas Hiller          8468695   
1253227     0          8473972        Jonas Hiller          8468695   
1253267     0          8470594   Marc-Andre Fleury          8459670   
1253350     0          8458988     Manny Fernandez          8470230   
1253380     0          8473404    Niklas Backstrom          8467423   
1253391     0          8473972        Jonas Hiller          8467396   
1253431     0          8469658      Cristobal Huet          8459587   
1253447     0          8471186          Yann Danis          8470604   
1253485     0          8460535       Jose Theodore          8462129   
1253487     1          8460535       Jose Theodore          8462129   
1253496     0          8473404    Niklas Backstrom          8470649   
1253557     0          8460703          Tim Thomas          8469639   
1253708     0          8459140  Nikolai Khabibulin          8459648   
1253806     0          8466141      Roberto Luongo          8467844   
1253821     0          8462117        Vesa Toskala          8470616   
1253832     0          8455710      Martin Brodeur          8467346   
1253838     1          8460712        Tomas Vokoun          8469639   
1253940     0          8462147    Miikka Kiprusoff          8459648   
1253941     0          8466141      Roberto Luongo          8470966   
1253982     1          8460703          Tim Thomas          8459457   
1253984     0          8462117        Vesa Toskala          8469464   
1253996     0          8470140       Kari Lehtonen          8465012   
1254002     0          8460703   

***Simulate the CDF based on xG Model***

In [172]:
import random as ran
from collections import Counter
from numpy import cumsum
from operator import itemgetter


dfsh = df_all_rows.groupby(['goalieIdForShot', 'uid','season']).agg({'goal':'sum','xGoal_GT':'sum'}).reset_index()
dfsh = dfsh.sort_values(by=['goalieIdForShot', 'uid'])
#print(dfsh)
goalie_list = dfsh.goalieIdForShot.unique().tolist()
#print(goalie_list)

final = {}
final_cdf_list = []
for x in goalie_list:#[8480420]:#
    print(x)
    dfp = dfsh[dfsh['goalieIdForShot'] == x].uid.tolist()
    #print(dfp)
    career_goals = []
    for y in dfp:
        dfa = df[(df['goalieIdForShot'] == x) & (df['uid'] == y)].xGoal.tolist()
        game_shots = []
        for z in dfa:
            res = []
            for i in range(10000):
                if ran.random() < z:
                    res.append(1)
                else:
                    res.append(0)
            game_shots.append(res)
        sim_goals = [sum(i) for i in zip(*game_shots)]
        career_goals.append(sim_goals)
    #print(career_goals)
    cum_goals = []
    for ind, b in enumerate(career_goals):
        t_goals = [sum(r) for r in zip(*career_goals[:ind+1])]
        add_up = dict(Counter(t_goals))
        cum_goals.append(dict(sorted(add_up.items())))
    #print(cum_goals)
    sortgoals = []
    for d in cum_goals:
        #unzip keys from values in a sorted order
        keys, values = zip(*sorted(d.items(), key=itemgetter(0)))
        total = sum(values)

        # calculate cumsum and zip with keys into new dict
        d_cump = dict(zip(keys, (subtotal/total for subtotal in cumsum(values))))
        sortgoals.append(d_cump)
    #print(sortgoals)
    dfg = dfsh[dfsh['goalieIdForShot'] == x].goal.tolist()
    dfc = cumsum(dfg)
    print(dfc)
    cdf = []
    for e, f in zip(dfc, sortgoals):
        if e > max(f, key=int):
            cdf.append(1)
        elif e < min(f, key=int):
            cdf.append(0)
        elif e in f:
            lookup = f[e]
            cdf.append(lookup)
        else:
            g = f.get(e, f[min(f.keys(), key=lambda k: abs(k-e))])
            cdf.append(g)
    final[x]= {'cdf': cdf, 'goals':list(dfc)}
    print(final[x])
    
    for i, j in enumerate(sortgoals):
        for k, v in j.items():
            final_cdf_list.append([x,i+1,k,v])
        


#print(final)
#print(final_cdf_list)


0
[  3   7   9  10  11  17  18  18  21  27  29  29  32  34  36  39  39  42
  44  46  47  50  50  53  56  56  60  62  63  66  70  71  71  71  71  72
  74  77  77  81  86  88  92  94  94  99 104 106 107 109 110 112 113 114
 118 120 122 125 127 129 131 134 137 140 144 149 152 152 152 152 152 153
 153 153 153]
{'cdf': [0.5671, 0.8696, 0.9314, 0.8894, 0.7631, 0.9057, 0.7925, 0.6771, 0.7453, 0.9358, 0.9461, 0.946, 0.9575, 0.9604, 0.9635, 0.98, 0.98, 0.9707, 0.9699, 0.914, 0.8803, 0.8301, 0.7507, 0.7987, 0.8102, 0.7447, 0.7642, 0.7081, 0.6572, 0.697, 0.7881, 0.8095, 0.6982, 0.6853, 0.5779, 0.5677, 0.5514, 0.6265, 0.593, 0.7218, 0.81, 0.7788, 0.8046, 0.8025, 0.7083, 0.8102, 0.8793, 0.9087, 0.9004, 0.9011, 0.8549, 0.7992, 0.7638, 0.7366, 0.8107, 0.7835, 0.7734, 0.8112, 0.7938, 0.7389, 0.7269, 0.7537, 0.7409, 0.8011, 0.853, 0.8961, 0.8921, 0.8913, 0.8886, 0.8886, 0.8884, 0.9048, 0.9029, 0.9028, 0.9015], 'goals': [3, 7, 9, 10, 11, 17, 18, 18, 21, 27, 29, 29, 32, 34, 36, 39, 39, 42, 44, 46, 47, 50

[  2   3   5   6   8   9  10  12  15  15  19  19  21  24  26  28  29  31
  34  34  35  36  37  42  46  46  48  49  54  57  60  64  64  65  68  69
  72  74  74  75  76  80  83  83  84  84  87  88  91  93  94  95  97 100
 102 103 103 103 106 107 110 112 115 117 120 124 127 130 135 137 138 144
 147 150 152 155 156 157 162 166 168 170 171 175 178 184 186 189 192 196
 198 201 206 207 211 211 218 220 220 222 225 228 230 234 236 237 240 243
 244 244 245 250 252 256 258 261 262 264 267 269 271 275 276 277 278 279
 282 286 286 288 290 294 296 298 303 305 308 311 313 314 314 315 320 322
 325 328 331 333 336 339 342 347 349 353 355 359 362 364 367 368 372 376
 379 379 382]
{'cdf': [0.8721, 0.4118, 0.4825, 0.4768, 0.4103, 0.3459, 0.1394, 0.0981, 0.1713, 0.1616, 0.218, 0.1878, 0.1493, 0.1952, 0.2637, 0.2592, 0.1472, 0.1428, 0.2029, 0.1238, 0.0912, 0.0821, 0.0764, 0.1951, 0.2498, 0.1578, 0.1436, 0.121, 0.1974, 0.2598, 0.3803, 0.425, 0.3451, 0.2838, 0.3016, 0.3062, 0.3603, 0.3352, 0.3138, 0.2299, 0.2

[ 1  5  5  7 10 14 14 17 17 18 20 23 26 30 32 36 37 38 39 40 42 44 44 48
 49]
{'cdf': [0.211, 0.4322, 0.2571, 0.2247, 0.2841, 0.5388, 0.5343, 0.7329, 0.725, 0.7433, 0.7102, 0.7092, 0.7416, 0.7881, 0.8357, 0.8299, 0.8579, 0.7611, 0.7348, 0.6748, 0.6602, 0.5873, 0.5796, 0.679, 0.7089], 'goals': [1, 5, 5, 7, 10, 14, 14, 17, 17, 18, 20, 23, 26, 30, 32, 36, 37, 38, 39, 40, 42, 44, 44, 48, 49]}
8459579
[  1   5   8   9  11  13  17  18  21  24  29  33  35  36  37  38  41  45
  46  47  51  56  61  61  66  67  69  72  78  81  85  86  87  89  94 100
 100 103 106 108 111 115 118 119 121 124 125 127 128 129 135 139 140 143
 149 153 157 159 164 165 166 169 169 172 176 179 182 185 186 187 190 192
 196 200 201 204 206 208 210]
{'cdf': [0.6407, 0.8792, 0.7611, 0.753, 0.7828, 0.6934, 0.8406, 0.6907, 0.8053, 0.8955, 0.9772, 0.9741, 0.9117, 0.8814, 0.8355, 0.7752, 0.7983, 0.8248, 0.7832, 0.7546, 0.8089, 0.8491, 0.9176, 0.8529, 0.9439, 0.9506, 0.9275, 0.9548, 0.9828, 0.9832, 0.9917, 0.9863, 0.981, 0.9664,

[  1   3   4   5   6   8  11  14  15  17  19  20  22  29  30  32  35  39
  40  43  47  50  53  55  57  57  60  61  66  69  70  74  75  76  77  80
  84  90  91  95  97 101 101 102 103 110 115 117 119 123 125 127 129 129
 131 132 134 138 140 141 142 143 147 151 155 158 159 162 162 162 165 166
 168 169 171 173 175 178 179 182 185 190 190 192 194 198 199 200 201 203
 207 210 212 216 217 218 221 225 226 227 229 230 230 234 236 239 240 243
 244 249 252 253 256 257 257 261 263 265 266 268 269 270 272 275 279 279
 281 284 288 290 296 296 300 302 305 307 308 310 311 311 311 317 320 321
 326 329 331 335 335 339 340 342 343 344 348 351 352 355 358 360 364 366
 369 371 373 375 379 382 382 385 388 388 389 390 391 391 391 393 396 400
 402 402 404 407 408 411 411 412 414 416 418 421 423 426 427 429 432 433
 436 439 439 444 444 446 448 450 451 453 454 460 461 465 469 470 471 472
 475 479 482 486 487 487 488 488 491 495 497 498 500 503 505 509 510 512
 515 518 520 521 522 526 531 531 535 536 541 541 54

[  2   3   9  10  12  14  18  18  19  23  25  27  31  32  35  37  38  38
  41  41  42  44  46  48  50  52  52  56  57  59  62  63  65  67  71  73
  73  75  77  80  82  83  85  90  94 100 102 103 103 108 110 112 113 116
 120 123 125 128 129 130 132 134 138 140 142 144 145 146 147 150 151 155
 157 158 160 163 163 166 166 170 172 175 177 180 182 186 187 188 190 191
 192 193 195 199 203 209 213 214 216 219 220 224 226 228 230 232 234 236
 236 240 241 247 249 249 251 252 254 257 261 262 263 266 271 272 272 272
 276 278 281 283 288 294 296 298 299 299 303 304 304 307 309 311 312 317
 320 322 323 324 329 329 333 337 339 342 345 348 350 354 359 360 364 367
 369 369 373 374 377 381 384 385 386 387 389 390 390 392 393 397 400 402
 406 410 412 414 416 421 423 424 426 428 430 432 434 435 440 441 445 446
 447 448 449 450 451 453 457 459 463 466 468 470 473 477 479 480 485 488
 492 495 499 504 505 505 507 512 514 519 520 522 524 526 531 532 533 533
 535 538 541 544 549 550 552 556 559 562 564 567 56

...

[  2   3   9  12  15  20  23  24  25  28  28  28  29  31  33  33  35  40
  41  47  49  53  58  61  63  64  66  70  72  73  76  77  78  80  84  87
  90  93  93  95  96  99 104 108 111 114 115 116 118 121]
{'cdf': [0.0311, 0.0128, 0.2148, 0.3468, 0.3627, 0.5349, 0.501, 0.4743, 0.5174, 0.5994, 0.4414, 0.4115, 0.3077, 0.3325, 0.4004, 0.2687, 0.3979, 0.5859, 0.5494, 0.6909, 0.6772, 0.6781, 0.8107, 0.832, 0.8106, 0.7182, 0.7172, 0.7447, 0.7799, 0.6772, 0.6701, 0.6238, 0.5675, 0.595, 0.6546, 0.5931, 0.6596, 0.7037, 0.5576, 0.5135, 0.4372, 0.3931, 0.4656, 0.3596, 0.3947, 0.3634, 0.3983, 0.3093, 0.2945, 0.3566], 'goals': [2, 3, 9, 12, 15, 20, 23, 24, 25, 28, 28, 28, 29, 31, 33, 33, 35, 40, 41, 47, 49, 53, 58, 61, 63, 64, 66, 70, 72, 73, 76, 77, 78, 80, 84, 87, 90, 93, 93, 95, 96, 99, 104, 108, 111, 114, 115, 116, 118, 121]}
8476319
[ 0  3  7  9 11 13 16]
{'cdf': [0.5158, 0.5199, 0.7194, 0.7578, 0.4938, 0.3379, 0.2904], 'goals': [0, 3, 7, 9, 11, 13, 16]}
8476330
[0]
{'cdf': [0.29], 'goals': [0]}

[  2   3   4   4   5  10  12  14  16  20  21  25  25  28  31  35  35  37
  40  43  43  45  48  48  52  58  60  62  64  67  70  71  72  76  79  81
  84  88  91  95  97  98 101 103 105 107 108 113 115 118 121 124 127 129
 133 135 139 141 146 149 152 155 159]
{'cdf': [0.8098, 0.5158, 0.3118, 0.0862, 0.124, 0.4007, 0.418, 0.2662, 0.1831, 0.3346, 0.3666, 0.4193, 0.2525, 0.3052, 0.4103, 0.472, 0.299, 0.3434, 0.3984, 0.4185, 0.3645, 0.3563, 0.3019, 0.2019, 0.3089, 0.4915, 0.5206, 0.4966, 0.4836, 0.5347, 0.5168, 0.449, 0.4002, 0.5585, 0.5646, 0.4954, 0.4988, 0.4916, 0.5894, 0.666, 0.6429, 0.6311, 0.6896, 0.6854, 0.7233, 0.6902, 0.6152, 0.6928, 0.6826, 0.739, 0.8017, 0.8566, 0.8199, 0.7563, 0.7897, 0.7476, 0.7176, 0.6783, 0.741, 0.7442, 0.7803, 0.8129, 0.7967], 'goals': [2, 3, 4, 4, 5, 10, 12, 14, 16, 20, 21, 25, 25, 28, 31, 35, 35, 37, 40, 43, 43, 45, 48, 48, 52, 58, 60, 62, 64, 67, 70, 71, 72, 76, 79, 81, 84, 88, 91, 95, 97, 98, 101, 103, 105, 107, 108, 113, 115, 118, 121, 124, 127, 129, 133,

[ 1  4  6  8  8 10 13 17 22 26 28 29]
{'cdf': [0.1312, 0.5268, 0.6536, 0.4303, 0.1824, 0.1885, 0.1976, 0.3606, 0.5991, 0.7982, 0.8098, 0.6726], 'goals': [1, 4, 6, 8, 8, 10, 13, 17, 22, 26, 28, 29]}
8476904
[0 0 4]
{'cdf': [0.641, 0.202, 0.8111], 'goals': [0, 0, 4]}
8476914
[  2   6   8  12  16  20  21  22  24  26  27  29  34  35  36  38  41  43
  45  49  53  54  57  59  62  65  67  72  73  76  77  78  82  88  88  92
  94  94  96 100 102 106 108 113 115 120 122 126 128 130 132 134 136 141
 142 146 151 156 157 161 165 170 173 175 179 183 187 190 193 196 200 201
 202 205 208 208 208 211 212 213 215 218 223 223 225 227 231 233 235]
{'cdf': [0.8685, 0.9696, 0.9156, 0.9458, 0.9755, 0.989, 0.8669, 0.811, 0.8752, 0.7752, 0.6628, 0.653, 0.7418, 0.5761, 0.4973, 0.331, 0.3475, 0.2974, 0.3159, 0.3347, 0.4308, 0.362, 0.3042, 0.2803, 0.237, 0.2366, 0.2225, 0.2772, 0.2539, 0.2944, 0.2166, 0.1664, 0.2152, 0.3117, 0.2895, 0.3156, 0.303, 0.2543, 0.2464, 0.2754, 0.2942, 0.3112, 0.2493, 0.2993, 0.2367, 0.

[  0   2   4   5   5   5   7   9  10  12  14  15  16  17  21  24  26  31
  32  33  36  38  41  41  42  46  49  53  54  57  59  61  64  66  68  75
  76  81  85  88  88  91  93  95  98  98 101 102 105 109 110 115 116 118
 118 118 124 126 126 127 132]
{'cdf': [0.2557, 0.5485, 0.2793, 0.1898, 0.0592, 0.0036, 0.0037, 0.0044, 0.0005, 0.0031, 0.0046, 0.0013, 0.0017, 0.0005, 0.003, 0.0096, 0.0092, 0.0549, 0.0599, 0.0427, 0.0477, 0.0365, 0.0487, 0.0228, 0.0167, 0.0307, 0.0273, 0.0235, 0.0159, 0.0105, 0.0113, 0.01, 0.0143, 0.0159, 0.0187, 0.05, 0.0493, 0.0704, 0.1108, 0.1169, 0.0933, 0.1123, 0.0738, 0.0798, 0.0738, 0.0415, 0.0506, 0.0394, 0.0317, 0.0533, 0.0217, 0.0441, 0.0529, 0.047, 0.0412, 0.0412, 0.0715, 0.0684, 0.0644, 0.0369, 0.0557], 'goals': [0, 2, 4, 5, 5, 5, 7, 9, 10, 12, 14, 15, 16, 17, 21, 24, 26, 31, 32, 33, 36, 38, 41, 41, 42, 46, 49, 53, 54, 57, 59, 61, 64, 66, 68, 75, 76, 81, 85, 88, 88, 91, 93, 95, 98, 98, 101, 102, 105, 109, 110, 115, 116, 118, 118, 118, 124, 126, 126, 127, 132

[ 4  9 10 16 21]
{'cdf': [0.6789, 0.8308, 0.8617, 0.9714, 0.9931], 'goals': [4, 9, 10, 16, 21]}
8477484
[ 3  8 13]
{'cdf': [0.7767, 0.9876, 0.9749], 'goals': [3, 8, 13]}
8477831
[ 1  6 12 13 16 18 20 22 24 28 31 33 36 36 38 40 43 44 48 55 58 61 65 67
 72 73 74 78 80]
{'cdf': [0.9727, 0.9319, 0.9513, 0.8585, 0.819, 0.7283, 0.6228, 0.5958, 0.5851, 0.7262, 0.8306, 0.7971, 0.7462, 0.4919, 0.3977, 0.3774, 0.3613, 0.3237, 0.367, 0.5904, 0.701, 0.7203, 0.7342, 0.7232, 0.7974, 0.7573, 0.7361, 0.7704, 0.7879], 'goals': [1, 6, 12, 13, 16, 18, 20, 22, 24, 28, 31, 33, 36, 36, 38, 40, 43, 44, 48, 55, 58, 61, 65, 67, 72, 73, 74, 78, 80]}
8477914
[1]
{'cdf': [0.9803], 'goals': [1]}
8477967
[ 4  7 12 15 16 18 23 25 27 29]
{'cdf': [0.7805, 0.8907, 0.9864, 0.9745, 0.9714, 0.9672, 0.9884, 0.9695, 0.9304, 0.9088], 'goals': [4, 7, 12, 15, 16, 18, 23, 25, 27, 29]}
8477968
[0 2]
{'cdf': [0.2896, 0.5363], 'goals': [0, 2]}
8477990
[1]
{'cdf': [0.8001], 'goals': [1]}
8478406
[ 2  3  3  5  5  5 10 10 12 17 20 23

In [173]:
final_df_cdf = pd.DataFrame(final_cdf_list, columns=['goalie_id', 'game_in_career', 'sim_goal_total','cdf_score'])
final_df_cdf["goalie_id"] = final_df_cdf["goalie_id"].map(int)
final_df_cdf['uid'] = final_df_cdf["goalie_id"].map(str) + final_df_cdf["game_in_career"].map(str)
final_df_cdf.to_csv('sim_cdf_dbf.csv')
final_df_cdf

goalie_id  game_in_career  sim_goal_total  cdf_score        uid
0                0               1               0     0.0277         01
1                0               1               1     0.1339         01
2                0               1               2     0.3284         01
3                0               1               3     0.5671         01
4                0               1               4     0.7646         01
5                0               1               5     0.8910         01
6                0               1               6     0.9580         01
7                0               1               7     0.9880         01
8                0               1               8     0.9977         01
9                0               1               9     0.9993         01
10               0               1              10     1.0000         01
11               0               2               0     0.0038         02
12               0               2               1     0.0279         02
13               0               2               2     0.0979         02
14               0               2               3     0.2264         02
15               0               2               4     0.4050         02
16               0               2               5     0.5929         02
17               0               2               6     0.7604         02
18               0               2               7     0.8696         02
19               0               2               8     0.9394         02
20               0               2               9     0.9765         02
21               0               2              10     0.9905         02
22               0               2              11     0.9970         02
23               0               2              12     0.9994         02
24               0               2              13     0.9998         02
25               0               2              14     1.0000         02
26               0               3               0     0.0010         03
27               0               3               1     0.0135         03
28               0               3               2     0.0488         03
29               0               3               3     0.1296         03
...            ...             ...             ...        ...        ...
3921337    8480420              18              66     0.9935  848042018
3921338    8480420              18              67     0.9954  848042018
3921339    8480420              18              68     0.9975  848042018
3921340    8480420              18              69     0.9985  848042018
3921341    8480420              18              70     0.9987  848042018
3921342    8480420              18              71     0.9991  848042018
3921343    8480420              18              72     0.9995  848042018
3921344    8480420              18              73     0.9998  848042018
3921345    8480420              18              76     0.9999  848042018
3921346    8480420              18              77     1.0000  848042018
3921347    8480925               1               0     0.2076   84809251
3921348    8480925               1               1     0.5520   84809251
3921349    8480925               1               2     0.8188   84809251
3921350    8480925               1               3     0.9441   84809251
3921351    8480925               1               4     0.9870   84809251
3921352    8480925               1               5     0.9974   84809251
3921353    8480925               1               6     0.9994   84809251
3921354    8480925               1               7     0.9999   84809251
3921355    8480925               1               9     1.0000   84809251
3921356    8480925               2               0     0.0663   84809252
3921357    8480925               2               1     0.2631   84809252
3921358    8480925               2               2     0.5269   84809252
3921359    8480925               2               3     0.7496   848

In [184]:
nextfinal = {k:v['cdf'] for k, v in final.items()}
nextfinal
finaldf = pd.DataFrame.from_dict(nextfinal,orient='index').transpose()
finaldf.to_csv('sim1.csv')
finaldf

0        8447687  8448382  8448535  8455710  8458568  8458988  8459140  \
0     0.5671   0.5608   0.9408   0.1591   0.8239   0.8721   0.9530   0.3220   
1     0.8696   0.8308   0.8185   0.1045   0.7427   0.4118   0.9171   0.6066   
2     0.9314   0.8922   0.6966   0.1060   0.8391   0.4825   0.9074   0.4266   
3     0.8894   0.8124   0.5302   0.4746   0.9813   0.4768   0.8590   0.3999   
4     0.7631   0.8793   0.4702   0.6667   0.9858   0.4103   0.8131   0.5196   
5     0.9057   0.8421   0.7332   0.6450   0.9957   0.3459   0.6978   0.4481   
6     0.7925   0.8845   0.7151   0.5443   0.9936   0.1394   0.8389   0.8265   
7     0.6771   0.8015   0.7559   0.4524   0.9943   0.0981   0.7874   0.8884   
8     0.7453   0.9275   0.5722   0.4974   0.9911   0.1713   0.6251   0.9377   
9     0.9358   0.9697   0.4998   0.6717   0.9852   0.1616   0.4190   0.9334   
10    0.9461   0.9659   0.5241   0.5353   0.9583   0.2180   0.3350   0.9724   
11    0.9460   0.9409   0.3507   0.5975   0.9872   0.1878   0.3613   0.9765   
12    0.9575   0.8893   0.4648   0.5579   0.9756   0.1493   0.2812   0.9878   
13    0.9604   0.9126   0.4648   0.7301   0.9719   0.1952   0.2483   0.9886   
14    0.9635   0.9147   0.3923   0.8440   0.9860   0.2637   0.3145   0.9580   
15    0.9800   0.8934   0.5283   0.8574   0.9815   0.2592   0.1459   0.9477   
16    0.9800   0.8996   0.7203   0.8232   0.9627   0.1472   0.0665   0.9279   
17    0.9707   0.8892   0.7048   0.8582   0.9304   0.1428   0.0504   0.9060   
18    0.9699   0.8761   0.6944   0.7707   0.8754   0.2029   0.0924   0.9393   
19    0.9140   0.8692   0.7867   0.8724   0.8263   0.1238   0.1177   0.9716   
20    0.8803   0.7948   0.7996   0.9083   0.8460   0.0912   0.0803   0.9750   
21    0.8301   0.6989   0.7978   0.9050   0.8027   0.0821   0.1479   0.9848   
22    0.7507   0.7263   0.8098   0.9048   0.8180   0.0764   0.1934   0.9815   
23    0.7987   0.7434   0.7853   0.9443   0.8693   0.1951   0.2258   0.9808   
24    0.8102   0.7350   0.7915   0.9615   0.8922   0.2498   0.2690   0.9689   
25    0.7447   0.7399   0.7789   0.9662   0.8719   0.1578   0.2500   0.9739   
26    0.7642   0.6364   0.8945   0.9793   0.8545   0.1436   0.2354   0.9645   
27    0.7081   0.5693   0.8947   0.9752   0.8688   0.1210   0.3873   0.9680   
28    0.6572   0.5372   0.8604   0.9794   0.8572   0.1974      NaN   0.9858   
29    0.6970   0.6621   0.9016   0.9780   0.9301   0.2598      NaN   0.9890   
..       ...      ...      ...      ...      ...      ...      ...      ...   
819      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
820      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
821      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
822      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
823      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
824      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
825      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
826      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
827      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
828      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
829      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
830      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
831      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
832      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
833      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
834      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
835      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
836      NaN      NaN      NaN      NaN      NaN      NaN      NaN      NaN   
837      NaN      NaN      NaN      NaN      NaN      N

In [174]:
final_db = []
for k, v in final.items():
    for i, (v1, v2) in enumerate(zip(v['goals'], v['cdf'])):
    #for i, x in enumerate(v):
        final_db.append([k,i+1,v1,v2])
final_db

[[0, 1, 3, 0.5671],
 [0, 2, 7, 0.8696],
 [0, 3, 9, 0.9314],
 [0, 4, 10, 0.8894],
 [0, 5, 11, 0.7631],
 [0, 6, 17, 0.9057],
 [0, 7, 18, 0.7925],
 [0, 8, 18, 0.6771],
 [0, 9, 21, 0.7453],
 [0, 10, 27, 0.9358],
 [0, 11, 29, 0.9461],
 [0, 12, 29, 0.946],
 [0, 13, 32, 0.9575],
 [0, 14, 34, 0.9604],
 [0, 15, 36, 0.9635],
 [0, 16, 39, 0.98],
 [0, 17, 39, 0.98],
 [0, 18, 42, 0.9707],
 [0, 19, 44, 0.9699],
 [0, 20, 46, 0.914],
 [0, 21, 47, 0.8803],
 [0, 22, 50, 0.8301],
 [0, 23, 50, 0.7507],
 [0, 24, 53, 0.7987],
 [0, 25, 56, 0.8102],
 [0, 26, 56, 0.7447],
 [0, 27, 60, 0.7642],
 [0, 28, 62, 0.7081],
 [0, 29, 63, 0.6572],
 [0, 30, 66, 0.697],
 [0, 31, 70, 0.7881],
 [0, 32, 71, 0.8095],
 [0, 33, 71, 0.6982],
 [0, 34, 71, 0.6853],
 [0, 35, 71, 0.5779],
 [0, 36, 72, 0.5677],
 [0, 37, 74, 0.5514],
 [0, 38, 77, 0.6265],
 [0, 39, 77, 0.593],
 [0, 40, 81, 0.7218],
 [0, 41, 86, 0.81],
 [0, 42, 88, 0.7788],
 [0, 43, 92, 0.8046],
 [0, 44, 94, 0.8025],
 [0, 45, 94, 0.7083],
 [0, 46, 99, 0.8102],
 [0, 47, 1

In [175]:
final_df = pd.DataFrame(final_db, columns=['goalie_id', 'game_in_career', 'actual_goals','cdf_score'])
final_df["goalie_id"] = final_df["goalie_id"].map(int)
final_df['uid'] = final_df["goalie_id"].map(str) + final_df["game_in_career"].map(str)
final_df.to_csv('sim_dbf.csv')
final_df

goalie_id  game_in_career  actual_goals  cdf_score        uid
0              0               1             3     0.5671         01
1              0               2             7     0.8696         02
2              0               3             9     0.9314         03
3              0               4            10     0.8894         04
4              0               5            11     0.7631         05
5              0               6            17     0.9057         06
6              0               7            18     0.7925         07
7              0               8            18     0.6771         08
8              0               9            21     0.7453         09
9              0              10            27     0.9358        010
10             0              11            29     0.9461        011
11             0              12            29     0.9460        012
12             0              13            32     0.9575        013
13             0              14            34     0.9604        014
14             0              15            36     0.9635        015
15             0              16            39     0.9800        016
16             0              17            39     0.9800        017
17             0              18            42     0.9707        018
18             0              19            44     0.9699        019
19             0              20            46     0.9140        020
20             0              21            47     0.8803        021
21             0              22            50     0.8301        022
22             0              23            50     0.7507        023
23             0              24            53     0.7987        024
24             0              25            56     0.8102        025
25             0              26            56     0.7447        026
26             0              27            60     0.7642        027
27             0              28            62     0.7081        028
28             0              29            63     0.6572        029
29             0              30            66     0.6970        030
...          ...             ...           ...        ...        ...
33083    8480382              33            93     0.8669  848038233
33084    8480382              34            94     0.8340  848038234
33085    8480382              35            97     0.8275  848038235
33086    8480382              36           102     0.8764  848038236
33087    8480382              37           103     0.7209  848038237
33088    8480382              38           108     0.7854  848038238
33089    8480382              39           110     0.7368  848038239
33090    8480382              40           110     0.6473  848038240
33091    8480382              41           112     0.6114  848038241
33092    8480382              42           115     0.5595  848038242
33093    8480420               1             2     0.7604   84804201
33094    8480420               2             7     0.9587   84804202
33095    8480420               3             8     0.6627   84804203
33096    8480420               4            10     0.5345   84804204
33097    8480420               5            12     0.3609   84804205
33098    8480420               6            15     0.2727   84804206
33099    8480420               7            18     0.1579   84804207
33100    8480420               8            22     0.2545   84804208
33101    8480420               9            26     0.4144   84804209
33102    8480420              10            27     0.4247  848042010
33103    8480420              11            30     0.3977  848042011
33104    8480420              12            35     0.6012  848042012
33105    8480420              13            38     0.6667  848042013
33106    8480420              14            41     0.5786  848042014
33107    8480420              15            47     0.7371  848042015
33108    8480420              16            50     0.8018  848042016
33109